# Amazon Best Sellers

# Import Libraries

In [3]:
from bs4 import BeautifulSoup
import requests
import pandas as pd
import numpy as np
import re
import matplotlib.pyplot as plt
import warnings
warnings.filterwarnings("ignore")
import seaborn as sns 
# this statement allows the visuals to render within your Jupyter Notebook
%matplotlib inline 
# You can configure the format of the images: ‘png’, ‘retina’, ‘jpeg’, ‘svg’, ‘pdf’.
%config InlineBackend.figure_format = 'png'

In [4]:
# Project for best sales in amazon.sa

# Best Sellers in Electronics (Page 1)

In [5]:
header = {'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/96.0.4664.45 Safari/537.36'}
url = "https://www.amazon.sa/-/en/gp/bestsellers/electronics/?ie=UTF8&ref_=sv_sv_elec_all_1"

In [6]:
response = requests.get(url, {'headers':header})
response.status_code

200

In [6]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

# BeautifulSoup Basics

In [7]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [8]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [9]:
soup.find_all('li', {'class':'zg-item-immersion'})[0].find_all('a')[1].text

'\n3.0 out of 5 stars\n'

In [10]:
# create function to clean data 

In [11]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [12]:
#Test with the first electroni product to ensure functions are working
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))


SAMSUNG Galaxy A12 Dual SIM Smartphone - 64GB, 4GB RAM, LTE, Black (KSA Version)
3.0 out of 5 stars
3.0
2
2
SAR 539.00
539.00


In [13]:
soup.find_all("li", class_ = "zg-item-immersion")[3] 

<li class="zg-item-immersion" role="gridcell"><span class="a-list-item"><div class="a-section a-spacing-none aok-relative"><div class="a-row a-spacing-none aok-inline-block"><span class="a-size-small aok-float-left zg-badge-body zg-badge-color"><span class="zg-badge-text">#4</span></span><span class="aok-float-left zg-badge-triangle zg-badge-color"></span></div><span class="aok-inline-block zg-item"><a class="a-link-normal" href="/-/en/SAMSUNG-Galaxy-M12-Dual-Smartphone/dp/B08XY5X3J7?_encoding=UTF8&amp;psc=1"><span class="zg-text-center-align"><div class="a-section a-spacing-small"><img alt="SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB, 4GB RAM, 4G LTE, Black (KSA Version)" height="200" src="https://images-na.ssl-images-amazon.com/images/I/81DCMeVrbKS._AC_UL200_SR200,200_.jpg" width="200"/></div></span>
<div aria-hidden="true" class="p13n-sc-truncate p13n-sc-line-clamp-2" data-rows="2">
            SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB, 4GB RAM, 4G LTE, Black (KSA Version)
   

In [14]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

    

In [15]:
products_list

[{'pro_name': 'SAMSUNG Galaxy A12 Dual SIM Smartphone - 64GB, 4GB RAM, LTE, Black (KSA Version)',
  'pro_rate': '3.0 out of 5 stars',
  'pro_rate_clean': '3.0',
  'review_num': '2',
  'review_num_clean': '2',
  'pro_price': 'SAR 539.00',
  'pro_price_clean': '539.00'},
 {'pro_name': 'Samsung Galaxy A12 LTE Dual SIM Smartphone - 64GB Storage, 4GB RAM, Blue (KSA Version)',
  'pro_rate': '1.0 out of 5 stars',
  'pro_rate_clean': '1.0',
  'review_num': '2',
  'review_num_clean': '2',
  'pro_price': 'SAR 539.00',
  'pro_price_clean': '539.00'},
 {'pro_name': 'Apple 20W USB-C Power Adapter, White',
  'pro_rate': '4.5 out of 5 stars',
  'pro_rate_clean': '4.5',
  'review_num': '358',
  'review_num_clean': '358',
  'pro_price': 'SAR 79.00',
  'pro_price_clean': '79.00'},
 {'pro_name': 'SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB, 4GB RAM, 4G LTE, Black (KSA Version)',
  'pro_rate': '4.0 out of 5 stars',
  'pro_rate_clean': '4.0',
  'review_num': '38',
  'review_num_clean': '38',
  'pro_price

In [16]:
products_df = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df

pro_name            pro_rate  \
0   SAMSUNG Galaxy A12 Dual SIM Smartphone - 64GB,...  3.0 out of 5 stars   
1   Samsung Galaxy A12 LTE Dual SIM Smartphone - 6...  1.0 out of 5 stars   
2                Apple 20W USB-C Power Adapter, White  4.5 out of 5 stars   
3   SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB,...  4.0 out of 5 stars   
4   SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB,...  4.2 out of 5 stars   
5                               New Apple Airpods Pro  4.3 out of 5 stars   
6   Anker PowerCore Select 20000, 20000mAh Power B...  4.1 out of 5 stars   
7   SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB,...  4.5 out of 5 stars   
8                    Apple AirPods with Charging Case  4.1 out of 5 stars   
9   Stylus Pen for iPad with Palm Rejection, Activ...  3.3 out of 5 stars   
10  JBL Flip 5 Portable Speaker Waterproof Wireles...  4.6 out of 5 stars   
11      Apple iPhone 12 With FaceTime (128GB) - White  4.4 out of 5 stars   
12  EZVIZ C6N Pan/Tilt Camera FHD Indoor,1080p WiF...  4.2 out of 5 stars   
13  Sony WH-1000XM4 Wireless Noise Cancelling Blue...  4.4 out of 5 stars   
14  Apple iPhone 12 Pro Max With FaceTime (128GB) ...  4.4 out of 5 stars   
15  Xiaomi Redmi 9A Dual SIM, 32GB, 2GB RAM, 4G LT...  4.0 out of 5 stars   
16  Apple iPhone 12 Pro With FaceTime (128GB) - Pa...  4.2 out of 5 stars   
17  Anker Alkaline AAA Batteries (8-Pack), Long-La...  4.6 out of 5 stars   
18  SAMSUNG 870 QVO SATA III 2.5" SSD 1TB (MZ-77Q1...  4.8 out of 5 stars   
19  EZVIZ C6N FHD Indoor Security Camera WiFi Smar...  4.3 out of 5 stars   
20  All-new Kindle Paperwhite (8GB) - Now with a 6...  4.4 out of 5 stars   
21  SoundPEATS Air3 Wireless Earbuds Mini Bluetoot...  4.0 out of 5 stars   
22       Apple iPhone 12 With FaceTime (128GB) - Blue  4.4 out of 5 stars   
23                         ستيك مي للتلفزيون من شاومي  4.0 out of 5 stars   
24                 JBL In-Ear Headphones, Black, T110  4.2 out of 5 stars   
25  Wireless Earbuds SoundPEATS TrueAir2 Bluetooth...  3.8 out of 5 stars   
26  Logitech M171 Wireless Mouse, 2.4 GHz with USB...  4.4 out of 5 stars   
27  SAMSUNG 980 PRO 500GB PCIe NVMe Gen4 Internal ...  4.8 out of 5 stars   
28  Anker Alkaline AA Batteries (8-Pack), Long-Las...  4.7 out of 5 stars   
29  Samsung Galaxy M11 Dual SIM - 32GB, 3GB RAM, 4...  4.0 out of 5 stars   
30  Anker USB C to Lightning Cable (6 ft), Powerli...  4.0 out of 5 stars   
31  Samsung Galaxy A72 | Ultra High-Res Quad Camer...  4.2 out of 5 stars   
32  Kingston A400 SATA SSD Solid State Drive 2.5 I...  4.5 out of 5 stars   
33  Anker PowerLine III USB-C to USB-C Cable USB-C...  5.0 out of 5 stars   
34  Anker Soundcore Life Q30 Bluetooth Headphones,...  4.6 out of 5 stars   
35  HyperX Cloud II Gaming Headset for PC & PS4 & ...  4.6 out of 5 stars   
36                 New Apple AirPods (3rd generation)  4.3 out of 5 stars   
37  Sony WI-C200 Wireless In-ear Bluetooth Headpho...  3.7 out of 5 stars   
38  Anker Alkaline AAA Batteries (4-Pack), Long-La...  4.5 out of 5 stars   
39  Apple Watch Series 6 (GPS, 44mm) - Space Grey ...  4.6 out of 5 stars   
40  Glorious Large Gaming Mouse Pad 11''x13'' - Black  4.7 out of 5 stars   
41  Samsung Galaxy Note20 5G, Pro Grade Triple Cam...  4.1 out of 5 stars   
42  Samsung Galaxy S21 Dual SIM - 128GB, 8GB RAM, ...  3.6 out of 5 stars   
43  Bluetooth Wireless Headphones 40 Hours Playtim...  4.3 out of 5 stars   
44  Apple iPhone 12 Pro Max With FaceTime (256GB) ...  4.4 out of 5 stars   
45  Xiaomi Redmi Note 10S, Dual SIM, 128GB, 6GB RA...  3.8 out of 5 stars   
46  Xiaomi POCO X3 Pro, Dual SIM, 256GB, 8GB RAM, ...  4.2 out of 5 stars   
47     Apple iPhone 12 With FaceTime (128GB) - Purple  4.4 out of 5 stars   
48  Wireless Earbuds True Wireless Bluetooth Earph...  4.0 out of 5 stars   
49  Xiaomi Mi Box S - 4K Ultra HDR Android TV Stre...  4.2 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             3.0          2           

# Best Sellers in   Electronics (Page 2)

In [18]:
url = 'https://www.amazon.sa/-/en/gp/bestsellers/electronics/ref=zg_bs_pg_2?ie=UTF8&pg=2'

In [19]:
response = requests.get(url)
response.status_code

200

In [20]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [21]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [22]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [23]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n3.6 out of 5 stars\n'

In [24]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [25]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Duracell Rechargeable AA 4 2500mAh
4.2 out of 5 stars
4.2
9
9
SAR 55.22
55.22


In [52]:
soup.find_all("li", class_ = "zg-item-immersion")[1] 

<li class="zg-item-immersion" role="gridcell"><span class="a-list-item"><div class="a-section a-spacing-none aok-relative"><div class="a-row a-spacing-none aok-inline-block"><span class="a-size-small aok-float-left zg-badge-body zg-badge-color"><span class="zg-badge-text">#2</span></span><span class="aok-float-left zg-badge-triangle zg-badge-color"></span></div><span class="aok-inline-block zg-item"><a class="a-link-normal" href="/%D9%84%D8%B9%D8%A8%D8%A9-%D9%81%D9%8A%D9%81%D8%A7-22-PlayStation-%D8%B3%D8%B9%D9%88%D8%AF%D9%8A%D8%A9/dp/B098KVCFM8?_encoding=UTF8&amp;psc=1"><span class="zg-text-center-align"><div class="a-section a-spacing-small"><img alt="لعبة فيفا 22 - PlayStation 4 (نسخة السعودية)" height="200" src="https://images-na.ssl-images-amazon.com/images/I/81OdjI%2Bq5-L._AC_UL200_SR200,200_.jpg" width="200"/></div></span>
<div aria-hidden="true" class="p13n-sc-truncate p13n-sc-line-clamp-1" data-rows="1">
            لعبة فيفا 22 - PlayStation 4 (نسخة السعودية)
        </div>
</

In [27]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [28]:
products_df = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df

pro_name            pro_rate  \
0                  Duracell Rechargeable AA 4 2500mAh  4.2 out of 5 stars   
1   Samsung Galaxy S21 5G | Pro Grade Triple Camer...  3.6 out of 5 stars   
2   TP-Link AC1750 Wi-Fi Range Extender - RE450, W...  4.0 out of 5 stars   
3   Samsung Galaxy A02 Dual SIM Smartphone - 32GB,...  3.6 out of 5 stars   
4                Glorious Model D Minus - Matte White  4.6 out of 5 stars   
5   SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
6   Samsung Galaxy S21 Ultra 5G Android Smartphone...  3.8 out of 5 stars   
7   Apple iPhone 12 Pro Max With FaceTime (128GB) ...  4.4 out of 5 stars   
8    New Apple iPhone 13 with FaceTime (256GB) - Blue  4.3 out of 5 stars   
9                                   Apple AirPods Pro  4.3 out of 5 stars   
10  Samsung EP-TA800 Travel Adapter for Super Fast...  4.4 out of 5 stars   
11  Samsung Galaxy Note20 5G, Pro Grade Triple Cam...  4.1 out of 5 stars   
12                                   New Apple AirTag  4.7 out of 5 stars   
13  ibsun Wireless Charger, 3 in 1 Wireless Chargi...  4.1 out of 5 stars   
14  UGREEN 65W USB C Charger Plug 4 Port GaN Type ...  4.2 out of 5 stars   
15  SAMSUNG 970 EVO Plus SSD 2TB - M.2 NVMe Interf...  4.9 out of 5 stars   
16  Sony MDR-ZX110AP Extra Bass Smartphone Headset...  4.1 out of 5 stars   
17  Anker 30W PIQ 3.0 USB-C Fast Charger Adapter, ...  4.4 out of 5 stars   
18  SanDisk Ultra Micro SD Card Android - Class 10...  4.4 out of 5 stars   
19  Anker 30W PIQ 3.0 USB-C Fast Charger Adapter, ...  4.4 out of 5 stars   
20  ELON Fast Charging Cable for iPhone USB to Lig...  4.3 out of 5 stars   
21  New Apple iPhone 13 Pro Max with FaceTime (128...  4.4 out of 5 stars   
22  UGREEN 2 Pack Screen Protector for iPhone 13/1...  4.4 out of 5 stars   
23  Samsung Galaxy S20 FE Dual SIM - 128GB, 8GB RA...  4.1 out of 5 stars   
24  SAMSUNG 980 PRO 1TB PCIe NVMe Gen4 Internal Ga...  4.8 out of 5 stars   
25      Apple iPhone 11 with FaceTime (128GB) - Black  4.3 out of 5 stars   
26  HP 652 Ink Advantage Cartridge, Tri-color - F6...  4.4 out of 5 stars   
27  HP 123 Black Original Ink Advantage Cartridge ...  4.1 out of 5 stars   
28  MSI MPG Z490 Gaming Plus Gaming Motherboard (A...  4.6 out of 5 stars   
29  SanDisk SSD PLUS 240GB - 2.5” SATA SSD, up to ...  4.7 out of 5 stars   
30  Bose Noise Cancelling Wireless Bluetooth Headp...  4.5 out of 5 stars   
31  HUAWEI FreeBuds 4i Wireless In-Ear Bluetooth E...  4.1 out of 5 stars   
32  Anker Nano iPhone Charger, 20W PIQ 3.0 Durable...  4.2 out of 5 stars   
33  4-Socket Extension Cord with Individual on/off...  4.5 out of 5 stars   
34  UGREEN Fast Car Charger Adapter 42.5W Dual USB...  4.3 out of 5 stars   
35  Apple Watch Series 6 (GPS, 40mm) - Gold Alumin...  4.6 out of 5 stars   
36  UGREEN iPhone Charger PD20W USB C iPhone 13 Fa...  4.2 out of 5 stars   
37  New Apple iPhone 13 Pro Max with FaceTime (256...  4.4 out of 5 stars   
38  HUAWEI HW-TIA-B09-BLACK WATCH FIT Smartwatch w...  4.5 out of 5 stars   
39  SanDisk Ultra Dual Drive USB Type-C Flash Driv...  4.4 out of 5 stars   
40  Stylus Pen for iPad with Palm Rejection，Active...  2.6 out of 5 stars   
41    HP 652 Ink Advantage Cartridge, Black - F6V25AE  4.3 out of 5 stars   
42      Apple iPhone 12 With FaceTime (128GB) - Black  4.4 out of 5 stars   
43  Anker USB C Charger, 20W PIQ 3.0 Fast Charger ...  4.2 out of 5 stars   
44  2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) -...  4.4 out of 5 stars   
45  Apple MagSafe Charger Qi/PMA for iPhone 13 Pro...  4.1 out of 5 stars   
46  SAMSUNG Galaxy Buds Pro, True Wireless Earbuds...  4.2 out of 5 stars   
47  Razer Seiren Mini - USB Condenser Microphone f...  4.6 out of 5 stars   
48  SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
49  TP-Link AC1200 Whole-Home Mesh Wi-Fi System(DE...  4.2 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.2          9           

# Best Sellers in Camera & Photo Products (Page 1)

In [150]:
url = 'https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966385031/ref=zg_bs_nav_1_electronics'

In [151]:
response = requests.get(url)
response.status_code

200

In [152]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [153]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [154]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [155]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.3 out of 5 stars\n'

In [156]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [157]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

EZVIZ C6N Pan/Tilt Camera FHD Indoor,1080p WiFi Smart Home Security Camera IR Night Vision Motion Detection Auto Tracking Baby/Elder/Pet Cloud Storage/SD Slot 2-Way Audio Wi-Fi 2.4G iOS Android App
4.2 out of 5 stars
4.2
1,408
1408
SAR 98.00
98.00


In [158]:
soup.find_all("li", class_ = "zg-item-immersion")[1] 

<li class="zg-item-immersion" role="gridcell"><span class="a-list-item"><div class="a-section a-spacing-none aok-relative"><div class="a-row a-spacing-none aok-inline-block"><span class="a-size-small aok-float-left zg-badge-body zg-badge-color"><span class="zg-badge-text">#2</span></span><span class="aok-float-left zg-badge-triangle zg-badge-color"></span></div><span class="aok-inline-block zg-item"><a class="a-link-normal" href="/-/en/EZVIZ-Indoor-Security-Camera-Android/dp/B07ZC1Q6W6?_encoding=UTF8&amp;psc=1"><span class="zg-text-center-align"><div class="a-section a-spacing-small"><img alt="EZVIZ C6N FHD Indoor Security Camera WiFi Smart 2.4G with iOS and Android App" height="200" src="https://images-na.ssl-images-amazon.com/images/I/51bA8A2cU9L._AC_UL200_SR200,200_.jpg" width="200"/></div></span>
<div aria-hidden="true" class="p13n-sc-truncate p13n-sc-line-clamp-2" data-rows="2">
            EZVIZ C6N FHD Indoor Security Camera WiFi Smart 2.4G with iOS and Android App
        </div

In [159]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [160]:
products_df = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df

pro_name            pro_rate  \
0   EZVIZ C6N Pan/Tilt Camera FHD Indoor,1080p WiF...  4.2 out of 5 stars   
1   EZVIZ C6N FHD Indoor Security Camera WiFi Smar...  4.3 out of 5 stars   
2   SanDisk Ultra Micro SD Card Android - Class 10...  4.4 out of 5 stars   
3         SanDisk Extreme microSDXC UHS-I Card- 128GB  4.4 out of 5 stars   
4   EZVIZ C2C 1080P Smart Home Security Wifi Camer...                 NaN   
5   6 PCS Camera Cover,Sliding Webcam Cover,Ultra ...  4.4 out of 5 stars   
6         SanDisk Extreme microSDXC UHS-I Card- 256GB  4.4 out of 5 stars   
7      Fujifilm Instax Mini, 10 sheet x 2 pack, White  4.6 out of 5 stars   
8   Eufy Indoor Cam 2K Pan & Tilt Home Security Ca...  4.5 out of 5 stars   
9   SanDisk Ultra microSDXC 128GB 100MB/s Class 10...  4.4 out of 5 stars   
10                 Rode Dynamic Podcasting Microphone  4.8 out of 5 stars   
11  Imou 360 Degree WiFi Security Camera, Up to 25...  3.1 out of 5 stars   
12  SanDisk 256GB Ultra® microSDXC 120MB/s A1 Clas...  4.4 out of 5 stars   
13  UGREEN 8K DisplayPort Cable Ultra HD DisplayPo...  4.6 out of 5 stars   
14  AmazonBasics High-Speed 4K HDMI Cable, 3 Feet,...  4.6 out of 5 stars   
15  SanDisk Ultra microSDXC 64GB 100MB/s Class 10 ...  4.4 out of 5 stars   
16    Kioxia Exceria 64GB MicroSD Card - LMEX1L064GG2  4.6 out of 5 stars   
17  DJI Osmo Mobile 3 Combo - 3-Axis Gimbal Stabil...  4.6 out of 5 stars   
18  AmazonBasics Braided 4K HDMI to HDMI Cable - 3...  4.7 out of 5 stars   
19  eufy Security 2K Indoor Cam Pan & Tilt, Home S...  4.6 out of 5 stars   
20  eufy Security, eufyCam 2 Pro Wireless Home Sec...  4.5 out of 5 stars   
21  SanDisk 128GB Ultra® microSDXC 120MB/s A1 Clas...  4.4 out of 5 stars   
22  Imou 4MP FHD 360 Degree Security Camera (White...  3.0 out of 5 stars   
23  EZVIZ Wifi Smart Security Camera 360 Degree, D...  4.2 out of 5 stars   
24  UGREEN 4K UHD DP to HDMI Cable Male to Male Di...  4.5 out of 5 stars   
25          SanDisk Extreme microSDXC UHS-I Card- 1TB  4.4 out of 5 stars   
26  YG-300 LCD Mini Portable Projector with USB/SD...  2.6 out of 5 stars   
27        Xiaomi Mi Home Security Camera 360° - White  4.0 out of 5 stars   
28  Sandisk Extreme microSDXC 128GB Plus SD Adapte...  4.8 out of 5 stars   
29  Imou 360 Degree Security Camera,Up to 256GB SD...  4.3 out of 5 stars   
30  eufy Security eufyCam 2 Wireless Home Security...  4.5 out of 5 stars   
31  Neewer 50-In-1 Action Camera Accessory Kit, Co...  4.4 out of 5 stars   
32  Panasonic Eneloop Pro Individual Cell Battery ...  4.0 out of 5 stars   
33  SanDisk Extreme PRO 256GB SDXC Memory Card up ...  4.8 out of 5 stars   
34  UGREEN 8K HDMI 2.1 Cable Ultra High-Speed 48Gb...  4.6 out of 5 stars   
35                5 in 1 Cleaning Kit for Camera Lens  4.0 out of 5 stars   
36        SanDisk Ultra 64GB SDXC Memory Card 120MB/s  4.7 out of 5 stars   
37  UGREEN 8K DisplayPort Cable Ultra HD DisplayPo...  4.6 out of 5 stars   
38  AccLoo WiFi Camera, HD 1080P Wireless Camera w...  3.8 out of 5 stars   
39  Xiaomi Mi Home Security Camera 360 Degrees 2K ...  4.2 out of 5 stars   
40  AccLoo Mini WiFi Camera, Security Camera HD 10...  3.6 out of 5 stars   
41  EZVIZ C6TC, 1080p WiFi Smart Home Security Cam...  4.4 out of 5 stars   
42  AccLoo Mini WiFi Camera, HD 1080P Wireless Por...  3.4 out of 5 stars   
43  2 * 2m/6.6 * 6.6ft Studio Backdrop Stand Brack...  3.3 out of 5 stars   
44  Andoer Photography Studio Cube Umbrella Softbo...  4.0 out of 5 stars   
45  Imou 4MP Full HD, IP 67 Outdoor Bullet Securit...  3.0 out of 5 stars   
46  eufy Security, eufyCam 2 Pro Wireless Home Sec...  4.5 out of 5 stars   
47  1.6 x 3M / 5 x 10FT Photography Studio Non-wov...  4.1 out of 5 stars   
48  110CM 43 5-in-1 Photography Studio Multi Photo...  4.1 out of 5 stars   
49  SanDisk 256GB High Endurance Video microSDXC C...  4.7 out of 5 stars   

   pro_rate_clean review_num review_num_clean   pro_price pro_price_clean  
0             4.2      1,408             

# Best Sellers in Camera & Photo Products (Page 2)

In [162]:
url ='https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966385031/ref=zg_bs_pg_2?ie=UTF8&pg=2'

In [163]:
response = requests.get(url)
response.status_code

200

In [164]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [174]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [166]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [167]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n5.0 out of 5 stars\n'

In [168]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [169]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

UGREEN 8K DisplayPort Cable Ultra HD Gold-Plated DisplayPort 1.4 Male to Male Nylon Braided Cable SPCC Shell, Support 7680x4320 Resolution 8K@60Hz, 4K@144Hz, 32.4Gbps HDP HDCP for HDTV Monitor-1Meter
4.1 out of 5 stars
4.1
80
80
SAR 56.80
56.80


In [170]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [171]:
products_df = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df

pro_name            pro_rate  \
0   UGREEN 8K DisplayPort Cable Ultra HD Gold-Plat...  4.1 out of 5 stars   
1   YSK-Replacement Remote control for Class pro s...  5.0 out of 5 stars   
2   UGREEN 8K HDMI 2.1 Male to Male Flat Cable Sup...  4.6 out of 5 stars   
3   todayto 30W Universal AC/DC, 3V 4.5V 6V 9V 12V...  3.5 out of 5 stars   
4        SanDisk Ultra 256GB SDXC Memory Card 120MB/s  4.7 out of 5 stars   
5         Canon EF 50mm f/1.8 STM Standard Lens,Black  4.8 out of 5 stars   
6       Flat Cable HDMI to HDMI 1080P 10 Meter, Black  3.6 out of 5 stars   
7    EZVIZ C6W Wifi Smart Home Indoor Security Camera  4.1 out of 5 stars   
8   AmazonBasics DisplayPort to HDMI Display Adapt...  4.1 out of 5 stars   
9   UGREEN Micro HDMI to HDMI Adapter Cable Male t...  4.6 out of 5 stars   
10  UGREEN 8K HDMI 2.1 Cable Ultra High-Speed 48Gb...  4.6 out of 5 stars   
11  Fujifilm Instax Mini Film For Instax Mini 7 / ...  4.4 out of 5 stars   
12  SanDisk Ultra MicroSDXC UHS-I Memory card 128G...  4.4 out of 5 stars   
13  SanDisk 32GB Ultra® microSDHC 120MB/s A1 Class...  4.4 out of 5 stars   
14  Security Camera Outdoor with Floodlight and So...  4.5 out of 5 stars   
15  Fake Dummy Safety Camera Simulation Hemisphere...  4.1 out of 5 stars   
16  UGREEN 4K HDMI Cable High-Speed HDMI Cord Nylo...  4.8 out of 5 stars   
17  TP-Link Tapo Smart Cam Pan Tilt Home WiFi Came...  4.7 out of 5 stars   
18  EZVIZ C1C-B WiFi Security Camera, 12 Meters Ni...  4.1 out of 5 stars   
19  Dahua 4CH 1080p CCTV Surveillance System Kit (...  3.5 out of 5 stars   
20  Waterproof Anti-Shock DSLR Camera Bag for Cano...  4.3 out of 5 stars   
21       SanDisk Ultra 128GB SDXC Memory Card 120MB/s  4.7 out of 5 stars   
22  AccLoo Kids Camera 1080P HD Digital Video Toy ...  3.8 out of 5 stars   
23  Honeywell UVEX Stealth Safety Goggles with Cle...                 NaN   
24  Fujifilm Instax Wide Film Twin Pack (White) (N...  4.8 out of 5 stars   
25  Viltrox Auto Focus EF-EOS M MOUNT Lens Mount A...  4.8 out of 5 stars   
26  UGREEN 8K HDMI Cable Ultra HD High Speed 48Gbp...  4.6 out of 5 stars   
27  40X60 HD Mini Day and Night Vision Monocular T...  3.1 out of 5 stars   
28  Professional Grade Lavalier Lapel Microphone O...  4.2 out of 5 stars   
29  JF-3110 35-102cm Aluminum Alloy Tripod Portabl...  2.4 out of 5 stars   
30  Microphone Stand Set Heavy Duty Mic Suspension...  3.5 out of 5 stars   
31       Celestron Portable Telescope Travel Scope 70  4.3 out of 5 stars   
32  Godox QR-P120 120CM 47.1 Inch Parabolic Softbo...                 NaN   
33  Ametoys 72 inches Projector Screen with Tripod...                 NaN   
34  Microphone Stand,Arabest Suspension Boom Sciss...  2.0 out of 5 stars   
35  UGREEN 8K DisplayPort Cable Ultra HD DisplayPo...  4.6 out of 5 stars   
36  suzicca EP7 2-Axis Gimbal Head Wearable Video ...                 NaN   
37  Professional Lavalier Microphone,AGPTEK Clip-o...  3.9 out of 5 stars   
38  2 Meters LED Strip Light, TV Bias Backlighting...  3.3 out of 5 stars   
39  Professional Camera Tripod Mount Stand Holder ...  2.1 out of 5 stars   
40  Moniss Battery & Charger Kit 2pcs 7.4V 1500mAh...                 NaN   
41  EZVIZ C3W Wifi Outdoor 1080p HD Security Camer...  4.3 out of 5 stars   
42        SanDisk Extreme microSDXC UHS-I Card- 512GB  4.4 out of 5 stars   
43  SanDisk 32GB Ultra microSDHC UHS-I Memory Card...  4.7 out of 5 stars   
44     Sony Cyber-Shot DSC-W800-20.1 MegaPixel, Black  4.0 out of 5 stars   
45  YUNSYE PTZ Camera Outdoor Dome IP Camera 1080P...  2.3 out of 5 stars   
46  UGREEN 8K HDMI 2.1 Male to Male Flat Cable Sup...  4.6 out of 5 stars   
47  Celestron - 70mm Travel Scope DX - Portable Re...  4.2 out of 5 stars   
48  DJI Action 2 Dual-Screen Combo - 4K Action Cam...  2.7 out of 5 stars   
49  Sandisk 128 GB Memory Card For Multi - Micro S...  4.2 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.1         80           

# Best Sellers in Binoculars, Telescopes & Optics (Page 1) 

In [193]:
url ="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966400031/ref=zg_bs_nav_2_16966385031"


In [194]:
response = requests.get(url)
response.status_code

200

In [195]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [196]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [197]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [198]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.3 out of 5 stars\n'

In [199]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [200]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

40X60 HD Mini Day and Night Vision Monocular Telescope with Tripod Phone Clip Handheld Optical Monocular Outdoor Camping
3.1 out of 5 stars
3.1
9
9
SAR 87.99
87.99


In [201]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [202]:
products_df = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df

pro_name            pro_rate  \
0   40X60 HD Mini Day and Night Vision Monocular T...  3.1 out of 5 stars   
1        Celestron Portable Telescope Travel Scope 70  4.3 out of 5 stars   
2   Celestron - 70mm Travel Scope DX - Portable Re...  4.2 out of 5 stars   
3   ComCreate 8X Folding High Powered Binoculars W...  1.0 out of 5 stars   
4        Celestron 93230 8 to 24mm 1.25 Zoom Eyepiece  4.7 out of 5 stars   
5   Celestron 93529 X-Cel LX 1.25-Inch 2x Barlow L...  4.7 out of 5 stars   
6            Celestron 21039 PowerSeeker 50 Telescope  4.1 out of 5 stars   
7                          Apple Pencil Tips - 4 pack  4.8 out of 5 stars   
8   10X25 Small Compact Lightweight Binoculars for...  3.3 out of 5 stars   
9   Nikon BAA807SB Fernglas Aculon A30 8x25 Binocu...  4.5 out of 5 stars   
10  Garberiel Monocular Telescope 12X50 High Power...  1.7 out of 5 stars   
11  Telescope, 70mm Aperture 400mm AZ Mount Astron...                 NaN   
12  (Single Pack) - Carson MicroBrite Plus 60 -120...  4.2 out of 5 stars   
13  Nikon 7246 Action 12x50 EX Extreme All-Terrain...  4.6 out of 5 stars   
14  Celestron - PowerSeeker 127EQ Telescope - Manu...  4.2 out of 5 stars   
15  NUZAMAS Astronomical Telescope for Educational...  3.2 out of 5 stars   
16  Celestron 21045 PowerSeeker 114EQ Telescope - ...  4.1 out of 5 stars   
17  Jiusion 40 to 1000x Magnification Endoscope, 2...  4.2 out of 5 stars   
18             Steiner 8X30 Sagor II Binocular, Green  5.0 out of 5 stars   
19  Celestron 93428 X-Cel LX 1.25-Inch 3x Barlow L...  4.6 out of 5 stars   
20  Baigaish Binocular 20x50 HD Professional/Water...                 NaN   
21    Celestron StarSense Explorer DX 130AZ Telescope  4.3 out of 5 stars   
22  NATIONAL GEOGRAPHIC Junior Metal Detector –Adj...  4.2 out of 5 stars   
23  8x21 Kids Binoculars Set - High Resolution Rea...  4.0 out of 5 stars   
24      Sunagor Mega Zoom Binoculars 30-160x70 ,Black  3.7 out of 5 stars   
25  Sunagor Compact Zoom Binoculars 25-110x30,Silv...  3.7 out of 5 stars   
26        Steiner 5845 7X50 Sagor II Binocular, Green  5.0 out of 5 stars   
27      Bushnell Legend Ultra HD Roof Prism Binocular  4.6 out of 5 stars   
28                        Celestron 1.25" Moon Filter  4.1 out of 5 stars   
29  Celestron – Outland X 8x42 Binoculars – Waterp...  4.5 out of 5 stars   
30  Celestron - 50mm Travel Scope - Portable Refra...  3.8 out of 5 stars   
31  Built in Motion Plus Remote and Nunchuck Contr...                 NaN   
32  Celestron - SkyMaster 25x70 Binocular - Large ...  4.4 out of 5 stars   
33  HEXEUM Night Vision Goggles Night Vision Binoc...  4.6 out of 5 stars   
34  Telescope Star Finder with Tripod F36050 HD Zo...  3.3 out of 5 stars   
35  Panasonic P-6JRC Replacement Water Filter Cart...  4.6 out of 5 stars   
36  SCOKC Binoculars 20x50 High Power, Compact HD ...  4.7 out of 5 stars   
37  HUTACT 10x42 Binoculars for Adults, with Stora...  4.4 out of 5 stars   
38  Camera Diaphragm, Compact Iris Aperture Adjust...                 NaN   
39  Gskyer Telescope, 70mm Aperture 400mm AZ Mount...  4.4 out of 5 stars   
40  ARCTIC P12 PWM (Black/Black) - Pressure-optimi...  4.6 out of 5 stars   
41  Mega Sports 10X25 Compact Binocular for Bird W...                 NaN   
42  12x42 Binoculars for Adults with New Smartphon...  4.8 out of 5 stars   
43  DMG-Digital Microscope 50x To 1000x Magnificat...  3.0 out of 5 stars   
44  Bushnell Falcon 10x50 Wide Angle Binoculars - ...  4.5 out of 5 stars   
45  Bysameyee USB Digital Microscope 40X to 1000X,...  3.0 out of 5 stars   
46  12X50 HD Monocular Telescope with Quick Smartp...                 NaN   
47  Newdoar 25x30 Zoomable Monocular Vintage Pirat...  4.2 out of 5 stars   
48                 Vortex Optics Solo Monocular 10x25  4.4 out of 5 stars   
49           Nikon Aculon A211 7x50 Binoculars, Black  4.6 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             3.1          9           

# Best Sellers in Binoculars, Telescopes & Optics (Page 2)

In [204]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966400031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [205]:
response = requests.get(url)
response.status_code

200

In [206]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [207]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [208]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [209]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n2.7 out of 5 stars\n'

In [ ]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [211]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

2021 Newest Telescope, 60mm Aperture 500mm AZ Mount Astronomical Refracting Telescope Adjustable Portable Telescopes with Adjustable Tripod, Phone Adapter, Nylon Bag…




SAR 527.46
527.46


In [212]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [213]:
products_df = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df

pro_name            pro_rate  \
0   2021 Newest Telescope, 60mm Aperture 500mm AZ ...                 NaN   
1   10X22 Binocular Telescope Night Version Foldab...  2.7 out of 5 stars   
2   SCOKC 10x-20x Zoom Binoculars Monocular HD Pow...  4.3 out of 5 stars   
3   Celestron - NexStar 127SLT Computerized Telesc...  4.3 out of 5 stars   
4   Celestron Upclose 20x50 Binoculars Porro Prism...  4.0 out of 5 stars   
5   Celestron – Outland X 10x50 Binoculars – Water...  4.5 out of 5 stars   
6           National Geographic 10x50 Porro Binocular  4.2 out of 5 stars   
7   Carson MicroFlip 100x-250x LED Lighted Pocket ...  4.1 out of 5 stars   
8                 Opticron BGA 10x42 Monocular, black  4.7 out of 5 stars   
9   Telescope Phone Mount, Universal Smart Phone A...  3.5 out of 5 stars   
10  SOOBA Astronomical Telescope Compact Portable ...                 NaN   
11             10X42 Darbel Bushnell Sport Roof Prism  3.6 out of 5 stars   
12  Steiner Marine Binoculars for Adults and Kids,...  4.8 out of 5 stars   
13  Celestron - PowerSeeker 70AZ Telescope - Manua...  4.2 out of 5 stars   
14  10x34 glasses type low light night vision tele...  2.4 out of 5 stars   
15  8"x8" Solar Filter Sheet for Telescopes, Binoc...                 NaN   
16  NIKULA metal High powered telescope zoom porta...  1.6 out of 5 stars   
17  Celestron 93524 Roof and Porro Binocular Tripo...  4.3 out of 5 stars   
18  Steiner 4477 10X26 Safari Ultrasharp Binocular...  4.5 out of 5 stars   
19             قاعدة تصوير دربيل او ناظور صيد احترافي                 NaN   
20   Bushnell Monoculars Telescope 16x52 Lens - Black  3.1 out of 5 stars   
21  Balacoo Monocular Telescope 40x60 High Definit...                 NaN   
22                        PROFESSIONAL COOLING SYSTEM  5.0 out of 5 stars   
23  Phone JJone APL-JS60XJJ09 Metal 60X HD Phone T...                 NaN   
24  Bushnell Equinox Z Night Vision 6X50 EQUINOX Z...  4.0 out of 5 stars   
25  ARCTIC ACFAN00135A P12 Value Pack - Pressure-O...  4.6 out of 5 stars   
26  KA Monocular Telescope fo Phone, 40X60 HD Mono...                 NaN   
27   Celestron 93317 Omni Series 1.25" (6mm) Eyepiece  4.6 out of 5 stars   
28  Celestron - PowerSeeker Telescope Accessory Ki...  4.6 out of 5 stars   
29  12X50 Powerful Binoculars, High Power HD Binoc...  4.3 out of 5 stars   
30  Celestron - Cometron 7x50 Bincoulars - Beginne...  4.6 out of 5 stars   
31                 Steiner Military-Marine Binoculars  4.6 out of 5 stars   
32  10x22 Binoculars Professional Telescope Zoom V...                 NaN   
33  Binoculars for Kids - HIGH Resolution, Shockpr...  4.5 out of 5 stars   
34  Astronomy Refractor Telescope, High Definition...                 NaN   
35         Panda 35x50 Adjustable Monocular Telescope  2.9 out of 5 stars   
36  National Geographic 90-01001 50/600 Refractor ...  3.8 out of 5 stars   
37  Bushnell Powerview Compact Folding Roof Prism ...  4.3 out of 5 stars   
38  60X60 Binoculars Telescope, Night Vision 10000...                 NaN   
39  DECUHTE Portable Mini Monocular Telescope with...                 NaN   
40  Vortex Optics Crossfire HD 10x50 Binoculars, B...  4.8 out of 5 stars   
41  Joshjt Telescope 70mm Aperture 400mm AZ Mount,...                 NaN   
42              Panda 35X50 Zoom Monoculars Telescope  2.1 out of 5 stars   
43  Scienish Telescope Travel Scope 90 X Refractor...  5.0 out of 5 stars   
44  60x60 binocular with coordinates night vision ...                 NaN   
45  Negaor Binoculars for Kids 8x21 High-Resolutio...                 NaN   
46  Negaor Binoculars for Kids 8x21 High-Resolutio...                 NaN   
47  Portable monocular, 40X60 HD Low-Light Night V...  1.0 out of 5 stars   
48  CHOSMO Dental Binocular Loupes 3.5X 420mm Dent...                 NaN   
49  Anjetan 1.25in Telescope Lens Creative Profess...                 NaN   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             NaN        NaN           

# Best Sellers in Computers, Components & Accessories (Page 1)

In [216]:
url= " https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966388031/ref=zg_bs_nav_1_electronics"

In [217]:
response = requests.get(url)
response.status_code

200

In [218]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [219]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [220]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [221]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.1 out of 5 stars\n'

In [223]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [224]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Stylus Pen for iPad with Palm Rejection, Active Pencil Compatible with (2018-2021) iPad Pro 11 & 12.9 inch, iPad 9th/8th/7th/6th Gen, iPad Air 4th/3rd Gen,iPad Mini 6th/5th Gen
3.3 out of 5 stars
3.3
5,545
5545
SAR 58.93
58.93


In [225]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [226]:
products_df = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df

pro_name            pro_rate  \
0   Stylus Pen for iPad with Palm Rejection, Activ...  3.3 out of 5 stars   
1   530pcs/set Heat Shrink Tubing Insulation Shrin...  4.1 out of 5 stars   
2   SAMSUNG 870 QVO SATA III 2.5" SSD 1TB (MZ-77Q1...  4.8 out of 5 stars   
3   Logitech M171 Wireless Mouse, 2.4 GHz with USB...  4.4 out of 5 stars   
4   SAMSUNG 980 PRO 500GB PCIe NVMe Gen4 Internal ...  4.8 out of 5 stars   
5   Anker USB C to Lightning Cable (6 ft), Powerli...  4.0 out of 5 stars   
6   Kingston A400 SATA SSD Solid State Drive 2.5 I...  4.5 out of 5 stars   
7   Anker PowerLine III USB-C to USB-C Cable USB-C...  5.0 out of 5 stars   
8   Glorious Large Gaming Mouse Pad 11''x13'' - Black  4.7 out of 5 stars   
9   TP-Link AC1750 Wi-Fi Range Extender - RE450, W...  4.0 out of 5 stars   
10               Glorious Model D Minus - Matte White  4.6 out of 5 stars   
11  SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
12  SAMSUNG 970 EVO Plus SSD 2TB - M.2 NVMe Interf...  4.9 out of 5 stars   
13  SanDisk Ultra Micro SD Card Android - Class 10...  4.4 out of 5 stars   
14  ELON Fast Charging Cable for iPhone USB to Lig...  4.3 out of 5 stars   
15  SAMSUNG 980 PRO 1TB PCIe NVMe Gen4 Internal Ga...  4.8 out of 5 stars   
16  HP 652 Ink Advantage Cartridge, Tri-color - F6...  4.4 out of 5 stars   
17  HP 123 Black Original Ink Advantage Cartridge ...  4.1 out of 5 stars   
18  MSI MPG Z490 Gaming Plus Gaming Motherboard (A...  4.6 out of 5 stars   
19  SanDisk SSD PLUS 240GB - 2.5” SATA SSD, up to ...  4.7 out of 5 stars   
20  4-Socket Extension Cord with Individual on/off...  4.5 out of 5 stars   
21  SanDisk Ultra Dual Drive USB Type-C Flash Driv...  4.4 out of 5 stars   
22  Stylus Pen for iPad with Palm Rejection，Active...  2.7 out of 5 stars   
23    HP 652 Ink Advantage Cartridge, Black - F6V25AE  4.3 out of 5 stars   
24  2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) -...  4.4 out of 5 stars   
25  Razer Seiren Mini - USB Condenser Microphone f...  4.6 out of 5 stars   
26  SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
27  TP-Link AC1200 Whole-Home Mesh Wi-Fi System(DE...  4.2 out of 5 stars   
28  WD 5TB My Passport Portable External Hard Driv...  4.3 out of 5 stars   
29  Anker Powerline Micro USB - Charging Cable, wi...  4.3 out of 5 stars   
30  UGREEN iPhone 13 Charger Cable [MFi Certified]...  4.1 out of 5 stars   
31  WD 2TB My Passport Portable External Hard Driv...  4.3 out of 5 stars   
32  UGREEN USB C Cable 2M, Braided 100W Power Deli...  4.2 out of 5 stars   
33         Anker Powerline+ II 6 Foot Lightning Cable  3.9 out of 5 stars   
34  Belkin USB-C to Lightning Cable (iPhone Fast C...  4.5 out of 5 stars   
35  AMD Ryzen 9 5900X 12-core, 24-Thread Unlocked ...  4.8 out of 5 stars   
36  UGREEN USB C Cable 3A Fast Charging Cable Nylo...  4.2 out of 5 stars   
37  Logitech G PRO X Gaming Headset 2nd Generation...  4.5 out of 5 stars   
38  Corsair Vengeance LPX 16GB (2 X 8GB) DDR4 3600...  4.8 out of 5 stars   
39  HyperX QuadCast - USB Condenser Gaming Microph...  4.8 out of 5 stars   
40  Fasgear USB C Cable for Oculus Quest Link 2, 9...  4.0 out of 5 stars   
41  Thermal Grizzly Kryonaut 12.5 W / m · K 1 g th...  4.7 out of 5 stars   
42        SanDisk Extreme microSDXC UHS-I Card- 128GB  4.4 out of 5 stars   
43  Toshiba 1TB Canvio Basics Portable USB3.0 Hard...  4.6 out of 5 stars   
44  SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
45  USB C 9-in1 Hub with 4K HDMI Adapter 100W PD C...  4.4 out of 5 stars   
46  UGREEN iPhone Lightning Cable 2M [MFi Certifie...  4.6 out of 5 stars   
47  TKOOFN Large RGB Colorful LED Light Keyboard M...  3.8 out of 5 stars   
48  Precision Screwdriver Set,ShowTop 110 in 1 Mag...  3.8 out of 5 stars   
49  Desk, Laptop Desk Bed Foldable Lazy Small Tabl...  3.9 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             3.3      5,545           

 # Best Sellers in Computers, Components & Accessories (Page 2)

In [228]:
url ="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966388031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [229]:
response = requests.get(url)
response.status_code

200

In [230]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [231]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [232]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [233]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.1 out of 5 stars\n'

In [234]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [235]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Laptop Stand, BiuLing Adjustable Portable Laptop Holder for Desk, Aluminum Foldable Laptop Riser with 6 Levels of Height Adjustment, Compatible with MacBook Air Pro, Dell, HP, Lenovo,10-15.6” Laptops
3.6 out of 5 stars
3.6
42
42
SAR 45.99
45.99


In [236]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [237]:
products_df = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df

pro_name            pro_rate  \
0   Laptop Stand, BiuLing Adjustable Portable Lapt...  3.6 out of 5 stars   
1   iPhone Charger Lightning Cable 10ft - by TalkW...  4.1 out of 5 stars   
2   Logitech Z150 Compact Multimedia Stereo Speake...  4.4 out of 5 stars   
3   SanDisk Ultra Dual Drive Luxe USB Type-C 128GB...  4.4 out of 5 stars   
4   ProCase iPad Air 4 Screen Protector 10.9 2020/...  4.6 out of 5 stars   
5   New Office 2021 Pro For Windows | Lifetime Act...  5.0 out of 5 stars   
6   [2 Pack] ProCase Galaxy Tab A7 10.4 2020 Scree...  4.3 out of 5 stars   
7   Samsung Electronics (MZ-V8V1T0B/AM) 980 SSD 1T...  4.8 out of 5 stars   
8   2021 Apple iPad Pro (11-inch, Wi-Fi, 128GB) - ...  4.6 out of 5 stars   
9   UGREEN USB C Cable USB A to Type C Data Cable ...  4.4 out of 5 stars   
10  UGREEN USB C Cable 3A Fast Charging Cable Nylo...  4.2 out of 5 stars   
11  SanDisk Ultra Dual Drive USB Type-C Flash Driv...  4.4 out of 5 stars   
12  Kingston 240GB A400 Sata 3 2.5 inch Internal S...  4.5 out of 5 stars   
13  UGREEN USB C Cable USB A to Type C Data Cable ...  4.4 out of 5 stars   
14          TP-LINK AC1200 Wi-Fi Range Extender RE305  4.1 out of 5 stars   
15                     ZORD M27 GAMING MONITOR 27INCH  3.8 out of 5 stars   
16  UGREEN USB C Cable 1M, Braided 100W Power Deli...  4.2 out of 5 stars   
17  HP 123 Tri-color Ink Cartridge, Cyan/Magenta/ ...  4.1 out of 5 stars   
18  90x40cm Old World Map mouse pad large pad to m...  4.3 out of 5 stars   
19  2Pack Apple Original Charger [Apple MFi Certif...  4.5 out of 5 stars   
20        SanDisk Extreme microSDXC UHS-I Card- 256GB  4.4 out of 5 stars   
21  Logitech MK235 Wireless Keyboard and Mouse Com...  3.8 out of 5 stars   
22  Extension Cord with USB, Power Strip with 3 Ou...  3.7 out of 5 stars   
23          SanDisk Cruzer Blade USB Flash Drive 64GB  4.5 out of 5 stars   
24  محرك أقراص صلبة داخلي باراكودا من سيجيت سعة 2 ...  4.7 out of 5 stars   
25  Large Gaming Mousepad World Map Game Mouse Pad...  4.3 out of 5 stars   
26  WD Blue SN550 500GB NVMe Internal SSD - Gen3 x...  4.6 out of 5 stars   
27  Stylus Pen for Touch Screens and Phone, Rechar...  3.8 out of 5 stars   
28  Thermal Printer USB High Speed 80mm طابعة فوات...                 NaN   
29  UGREEN USB C Hard Drive Enclosure USB 3.1 Gen ...  4.6 out of 5 stars   
30  4 Pack Cable Management Sleeve, Cord Organizer...  4.2 out of 5 stars   
31     Anker PowerLine Micro USB 3ft White Offline V3  4.1 out of 5 stars   
32  Mainstayae High Speed 4 Port USB 3.0 Multi HUB...  3.5 out of 5 stars   
33  AccLoo Single Monitor Desk Mount Stand - Full ...  4.7 out of 5 stars   
34  UGREEN iPhone Charging Cable [Apple MFi Certif...  4.5 out of 5 stars   
35  Asus Gaming Monitor - 27inch, Full HD, 0.5ms, ...  4.6 out of 5 stars   
36  UGREEN USB C Cable USB A to Type C Data Cable ...  4.4 out of 5 stars   
37  Corsair XTM50 High Performance Ultra-Low Therm...  4.7 out of 5 stars   
38  UGREEN USB Bluetooth 4.0 Adapter USB Wireless ...  4.1 out of 5 stars   
39  SanDisk Ultra microSDXC 128GB 100MB/s Class 10...  4.4 out of 5 stars   
40  UGREEN Phone Mount Tablet Holder 360 Adjustabl...  4.2 out of 5 stars   
41  SanDisk 500GB Extreme Portable External SSD - ...  4.7 out of 5 stars   
42  Stylus Pen for iPad with Palm Rejection, Activ...  4.6 out of 5 stars   
43                 Cable Ties Black 4 x 100millimeter  4.1 out of 5 stars   
44  Lenovo Smart Tab M10 Plus, 10.3" Android Table...  4.2 out of 5 stars   
45  UGREEN 7-in-1 USB C Hub 4K@60Hz Type C to HDMI...  4.2 out of 5 stars   
46  UGREEN Micro USB Cable Nylon Braided Fast Quic...  4.6 out of 5 stars   
47  Stylus Pen for iPad with Palm Rejection, Activ...  3.3 out of 5 stars   
48  UGREEN iPhone Lightning Cable 1M [MFi Certifie...  4.6 out of 5 stars   
49  ZORD PHANTOM-1 GAMING PC, RYZEN 3 3200G, 16GB ...  3.3 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             3.6         42           

# Best Sellers in Headphones, Earbuds & Accessories (Page 1 )

In [238]:
url = "https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966390031/ref=zg_bs_pg_1?ie=UTF8&pg=1"

In [239]:
response = requests.get(url)
response.status_code

200

In [240]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [241]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [242]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [243]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.1 out of 5 stars\n'

In [244]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [245]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

New Apple Airpods Pro
4.3 out of 5 stars
4.3
2,350
2350
SAR 749.00
749.00


In [246]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [247]:
products_df = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df

pro_name            pro_rate  \
0                               New Apple Airpods Pro  4.3 out of 5 stars   
1                    Apple AirPods with Charging Case  4.1 out of 5 stars   
2   Sony WH-1000XM4 Wireless Noise Cancelling Blue...  4.4 out of 5 stars   
3   SoundPEATS Air3 Wireless Earbuds Mini Bluetoot...  4.0 out of 5 stars   
4                  JBL In-Ear Headphones, Black, T110  4.2 out of 5 stars   
5   Wireless Earbuds SoundPEATS TrueAir2 Bluetooth...  3.8 out of 5 stars   
6   Anker Soundcore Life Q30 Bluetooth Headphones,...  4.6 out of 5 stars   
7   HyperX Cloud II Gaming Headset for PC & PS4 & ...  4.6 out of 5 stars   
8                  New Apple AirPods (3rd generation)  4.3 out of 5 stars   
9   Sony WI-C200 Wireless In-ear Bluetooth Headpho...  3.7 out of 5 stars   
10  Bluetooth Wireless Headphones 40 Hours Playtim...  4.3 out of 5 stars   
11  Wireless Earbuds True Wireless Bluetooth Earph...  4.0 out of 5 stars   
12                                  Apple AirPods Pro  4.3 out of 5 stars   
13  Sony MDR-ZX110AP Extra Bass Smartphone Headset...  4.1 out of 5 stars   
14  Bose Noise Cancelling Wireless Bluetooth Headp...  4.5 out of 5 stars   
15  HUAWEI FreeBuds 4i Wireless In-Ear Bluetooth E...  4.1 out of 5 stars   
16  SAMSUNG Galaxy Buds Pro, True Wireless Earbuds...  4.2 out of 5 stars   
17  Bose QuietComfort Earbuds - True Wireless Nois...  4.4 out of 5 stars   
18  Hybrid Active Noise Cancelling Headphones with...  4.8 out of 5 stars   
19  Wireless Earbuds SoundPEATS TrueAir2 Bluetooth...  3.8 out of 5 stars   
20    Apple Lightning to 3.5mm Headphone Jack Adapter  4.2 out of 5 stars   
21  Wireless Earbuds, SOUNDPEATS S5 Over-Ear Hooks...  4.4 out of 5 stars   
22  Wired Lightning Headset Earphone for Apple iPh...  2.0 out of 5 stars   
23  Bose Noise Cancelling Wireless Bluetooth Headp...  4.5 out of 5 stars   
24  Joyroom JR-T03S TWS Bluetooth True Wireless St...  2.7 out of 5 stars   
25    Huawei Sport lite Bluetooth Headset AM61, Black  4.0 out of 5 stars   
26  For iPhone X 8 7 Plus Bluetooth Earphones Wire...  2.5 out of 5 stars   
27  JBL T110 Wired Universal In-Ear Headphone with...  4.2 out of 5 stars   
28  JBL TUNE115TWS True Wireless Earbuds Black, small  4.0 out of 5 stars   
29  Sony WH-1000XM4 Wireless Noise Cancelling Blue...  4.5 out of 5 stars   
30  Sony MDR-ZX110AP Wired On-Ear Headphones with ...  4.1 out of 5 stars   
31  HUAWEI BLUETOOTH HEADPHONE LITE AM61 MOONLIGHT...  4.3 out of 5 stars   
32  Bluetooth Earphones, SoundPEATS Dual Dynamic D...  4.2 out of 5 stars   
33  Anker Soundcore Liberty Air 2 Pro True Wireles...  4.1 out of 5 stars   
34  Razer Kraken - Wired Gaming Headset for Multip...  4.4 out of 5 stars   
35  Wireless Earbuds SOUNDPEATS Sonic in-Ear Wirel...  3.9 out of 5 stars   
36          JBL In-Ear Headphones, RED - T110, Normal  4.2 out of 5 stars   
37                HyperX Cloud Alpha S Gaming Headset  4.5 out of 5 stars   
38  Wireless Earbuds SoundPEATS TrueAir2 Bluetooth...  3.8 out of 5 stars   
39  Huawei Stereo Earphones with Remote and Microp...  4.1 out of 5 stars   
40  Wireless Earbuds, SOUNDPEATS Q Bluetooth 5.0 H...  4.1 out of 5 stars   
41      TOSHIBA RZE-BT1200H Wireless Headphones Black  4.5 out of 5 stars   
42  Anker Soundcore Liberty Air 2 Pro True Wireles...  4.4 out of 5 stars   
43  Joyroom JR-T03S In-Ear Detection True Wireless...  2.8 out of 5 stars   
44  Wireless Earbuds SoundPEATS TrueCapsule2 with ...  3.7 out of 5 stars   
45  Wireless Earbuds SoundPEATS T2 Hybrid Active N...  4.2 out of 5 stars   
46  Datazone Ear phone Headphones,crystal clear so...  3.6 out of 5 stars   
47  Amoi F9 Bluetooth 5.0 Wireless Earbuds,IPX7 Wa...  2.8 out of 5 stars   
48  Lenovo Earphone Bluetooth5.0 Wireless Headset ...  3.1 out of 5 stars   
49  AirPods Pro Case Cover with Keychain Full Prot...  4.3 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.3      2,350           

# Best Sellers in Headphones, Earbuds & Accessories (Page 2 )

In [248]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966390031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [249]:
response = requests.get(url)
response.status_code

200

In [250]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [251]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [252]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [253]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.0 out of 5 stars\n'

In [254]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [255]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Huawei Honor xsport Bluetooth Headset am61 IPX5 Waterproof BT4.1 Music Mic Control Wireless Earphone For android
2.7 out of 5 stars
2.7
3
3
SAR 115.00
115.00


In [256]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [257]:
products_df = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df

pro_name            pro_rate  \
0   Huawei Honor xsport Bluetooth Headset am61 IPX...  2.7 out of 5 stars   
1   JBL TUNE 700BT WIRELESS OVER-EAR HEADPHONE - B...  4.0 out of 5 stars   
2   True Wireless Earphones, Bluetooth 5 earbuds w...  4.3 out of 5 stars   
3   Nylon Case For Apple Air Pods Protective Bluet...  2.3 out of 5 stars   
4   beats Flex – All-Day Wireless Earphones – beat...  3.4 out of 5 stars   
5   JBL T110 Wired Universal In-Ear Headphone with...  4.3 out of 5 stars   
6   SKULLCANDY Dime True Wireless In-Ear Earbuds W...  4.1 out of 5 stars   
7   Sony WH-CH510 Wireless Bluetooth On-Ear with M...  3.6 out of 5 stars   
8   HUAWEI FreeBuds 4 Wireless Bluetooth Open-fit ...  4.0 out of 5 stars   
9   Sony WI-XB400 Wireless Extra Bass in-Ear Headp...  3.7 out of 5 stars   
10  JOYROOM JR-T03s white Wireless bluetooth headp...  2.7 out of 5 stars   
11          Nokia Lite Earbuds BH-205 - Black, Normal  3.2 out of 5 stars   
12  New bee Bluetooth Earpiece V5.0 Wireless Hands...  4.1 out of 5 stars   
13  JBL KIDS WIRELESS ON-EAR HEADPHONE JR310BT - Blue  4.6 out of 5 stars   
14  Sony WH-CH510 Wireless Bluetooth On-Ear with M...  3.6 out of 5 stars   
15  UGREEN Wireless Earbuds HiTune Bluetooth 5.0 E...  4.3 out of 5 stars   
16  Anker Soundcore Life P2 Wireless Earbuds with ...  4.2 out of 5 stars   
17                       Red Magic TWS Gsming Earbuds  3.4 out of 5 stars   
18  SoundPEATS H2 Hybrid Dual Driver Wireless Earb...  5.0 out of 5 stars   
19  Sony WF-1000XM3 True Wireless Noise Cancelling...  3.9 out of 5 stars   
20  Display Headphone Stand Headset Holder Earphon...  4.3 out of 5 stars   
21  Silicone Case for AirPods Pro, Protective Shoc...  3.9 out of 5 stars   
22  Wireless Stereo Headphone From Toshiba Rze-Bt1...  3.4 out of 5 stars   
23  OnePlus Buds Z - True Wireless in-Ear Earbuds ...  4.3 out of 5 stars   
24  Anker Soundcore Life P2 Wireless Earbuds with ...  4.2 out of 5 stars   
25  SoundPEATS Wireless Earbuds Bluetooth 5.0 Head...  3.9 out of 5 stars   
26  Xiaomi Mi True Wireless Earbuds Basic, Black -...  2.6 out of 5 stars   
27  Wireless Earbuds, SoundPEATS T3 Active Noise C...  4.4 out of 5 stars   
28  SoundPEATS H1 Wireless Earbuds, Bluetooth V5.2...  4.0 out of 5 stars   
29  HUAWEI FreeBuds Pro Bluetooth Wireless Earphon...  4.4 out of 5 stars   
30  F9-5B TWS Earphone with Power Bank Hifi True S...  3.5 out of 5 stars   
31  Toshiba Noise Cancelling Bluetooth Headphones ...  3.5 out of 5 stars   
32  JBL T510 WIRELESS ON-EAR HEADPHONE WITH MIC - ...  4.6 out of 5 stars   
33                    Anker Soundcore Icon Mini - Red  3.2 out of 5 stars   
34  Samsung Basic Mass Wired In Earphones, White -...  5.0 out of 5 stars   
35  Wireless Earbuds, SOUNDPEATS Q Bluetooth 5.0 H...  4.1 out of 5 stars   
36  Samsung Galaxy SM-R175 Wireless Buds Plus with...  4.2 out of 5 stars   
37  SoundPEATS TrueFree2 Wireless Earbuds Bluetoot...  4.0 out of 5 stars   
38  Sony WF-1000XM4 Industry Leading Noise Cancell...  3.9 out of 5 stars   
39  Case Cover for Airpods Pro Game Console Silico...  3.1 out of 5 stars   
40  SAMSUNG Galaxy Buds2 Earbuds with Charging Cas...  4.2 out of 5 stars   
41                         Apple AirPods Max - Silver  4.0 out of 5 stars   
42  Datazone AirPods, TWS Wireless Earbuds Compati...  3.3 out of 5 stars   
43  G9000 Stereo Gaming Headset for PS4, PC, Xbox ...  3.5 out of 5 stars   
44          Apple AirPods with Wireless Charging Case  3.6 out of 5 stars   
45  HUAWEI FreeBuds 4i Wireless In-Ear Bluetooth E...  4.4 out of 5 stars   
46  Sony WF-C500 True Wireless Headphones - Up to ...                 NaN   
47  AccLoo Wireless Earbuds Bluetooth 5.0 Headphon...  3.9 out of 5 stars   
48  Sony MDREX15APBLACK Wired In-Ear Headphones EX...  3.9 out of 5 stars   
49  Sony WI-C200 Wireless In-ear Bluetooth Headpho...  3.7 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             2.7          3           

# Best Sellers in Mobile Phones & Communication Products (Page 1 )

In [3]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966387031/ref=zg_bs_nav_1_electronics"

In [4]:
response = requests.get(url)
response.status_code

200

In [5]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [13]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [7]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [8]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n1.0 out of 5 stars\n'

In [9]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [10]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

SAMSUNG Galaxy A12 Dual SIM Smartphone - 64GB, 4GB RAM, LTE, Black (KSA Version)
3.0 out of 5 stars
3.0
2
2
SAR 539.00
539.00


In [11]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [12]:
products_df = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df

pro_name            pro_rate  \
0   SAMSUNG Galaxy A12 Dual SIM Smartphone - 64GB,...  3.0 out of 5 stars   
1   Samsung Galaxy A12 LTE Dual SIM Smartphone - 6...  1.0 out of 5 stars   
2                Apple 20W USB-C Power Adapter, White  4.5 out of 5 stars   
3   SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB,...  4.0 out of 5 stars   
4   Anker PowerCore Select 20000, 20000mAh Power B...  4.1 out of 5 stars   
5   SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB,...  4.2 out of 5 stars   
6                               New Apple Airpods Pro  4.3 out of 5 stars   
7   SAMSUNG Galaxy M12 Dual SIM Smartphone - 64GB,...  4.5 out of 5 stars   
8                    Apple AirPods with Charging Case  4.1 out of 5 stars   
9   JBL Flip 5 Portable Speaker Waterproof Wireles...  4.6 out of 5 stars   
10  Xiaomi Redmi 9A Dual SIM, 32GB, 2GB RAM, 4G LT...  4.0 out of 5 stars   
11  Sony WH-1000XM4 Wireless Noise Cancelling Blue...  4.4 out of 5 stars   
12  Apple Watch Series 6 (GPS, 44mm) - Space Grey ...  4.6 out of 5 stars   
13      Apple iPhone 12 With FaceTime (128GB) - White  4.4 out of 5 stars   
14  Apple iPhone 12 Pro Max With FaceTime (128GB) ...  4.4 out of 5 stars   
15  SoundPEATS Air3 Wireless Earbuds Mini Bluetoot...  4.0 out of 5 stars   
16  Apple iPhone 12 Pro With FaceTime (128GB) - Pa...  4.2 out of 5 stars   
17       Apple iPhone 12 With FaceTime (128GB) - Blue  4.4 out of 5 stars   
18  Wireless Earbuds SoundPEATS TrueAir2 Bluetooth...  3.8 out of 5 stars   
19                 JBL In-Ear Headphones, Black, T110  4.2 out of 5 stars   
20  Sony WI-C200 Wireless In-ear Bluetooth Headpho...  3.7 out of 5 stars   
21  Anker PowerLine III USB-C to USB-C Cable USB-C...  5.0 out of 5 stars   
22  Samsung Galaxy M11 Dual SIM - 32GB, 3GB RAM, 4...  4.0 out of 5 stars   
23  Anker Soundcore Life Q30 Bluetooth Headphones,...  4.6 out of 5 stars   
24   New Apple iPhone 13 with FaceTime (256GB) - Blue  4.3 out of 5 stars   
25  Anker USB C to Lightning Cable (6 ft), Powerli...  4.0 out of 5 stars   
26                 New Apple AirPods (3rd generation)  4.3 out of 5 stars   
27  HyperX Cloud II Gaming Headset for PC & PS4 & ...  4.6 out of 5 stars   
28  Samsung Galaxy A72 | Ultra High-Res Quad Camer...  4.2 out of 5 stars   
29  Apple Watch Series 6 (GPS, 40mm) - Gold Alumin...  4.6 out of 5 stars   
30  Samsung Galaxy S21 5G | Pro Grade Triple Camer...  3.6 out of 5 stars   
31  Anker 30W PIQ 3.0 USB-C Fast Charger Adapter, ...  4.4 out of 5 stars   
32  Wireless Earbuds True Wireless Bluetooth Earph...  4.0 out of 5 stars   
33  Anker PowerCore III 10K, Wireless Portable Cha...  4.7 out of 5 stars   
34  Bose Noise Cancelling Wireless Bluetooth Headp...  4.5 out of 5 stars   
35  Samsung Galaxy S21 Ultra 5G Android Smartphone...  3.8 out of 5 stars   
36  Apple iPhone 12 Pro Max With FaceTime (256GB) ...  4.4 out of 5 stars   
37  Sony MDR-ZX110AP Extra Bass Smartphone Headset...  4.1 out of 5 stars   
38  Samsung Galaxy S20 FE 4G Android Smartphone, 1...                 NaN   
39  Samsung Galaxy Note20 5G, Pro Grade Triple Cam...  4.1 out of 5 stars   
40  UGREEN 2 Pack Screen Protector for iPhone 13/1...  4.4 out of 5 stars   
41  Xiaomi Redmi Note 10S, Dual SIM, 128GB, 6GB RA...  3.8 out of 5 stars   
42  Bluetooth Wireless Headphones 40 Hours Playtim...  4.3 out of 5 stars   
43  Samsung Galaxy S21 Dual SIM - 128GB, 8GB RAM, ...  3.6 out of 5 stars   
44  Apple iPhone 12 Pro Max With FaceTime (128GB) ...  4.4 out of 5 stars   
45  Samsung Galaxy Note20 5G, Pro Grade Triple Cam...  4.1 out of 5 stars   
46  Anker 30W PIQ 3.0 USB-C Fast Charger Adapter, ...  4.4 out of 5 stars   
47  UGREEN 65W USB C Charger Plug 4 Port GaN Type ...  4.2 out of 5 stars   
48  Samsung Galaxy A02 Dual SIM Smartphone - 32GB,...  3.6 out of 5 stars   
49  Xiaomi POCO X3 Pro, Dual SIM, 256GB, 8GB RAM, ...  4.2 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             3.0          2           

# Best Sellers in Mobile Phones & Communication Products (Page 2 )

In [14]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966387031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [15]:
response = requests.get(url)
response.status_code

200

In [16]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [17]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [18]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [19]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.3 out of 5 stars\n'

In [20]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [21]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

UGREEN iPhone Protective Case Compatible for iPhone 13 Pro Clear Case with Shock Absorption Anti Scratch TPU Precise Cutouts and Slim Fit Case Easy to Install iPhone 13 Pro Transparent Cover 6.1 inch
4.5 out of 5 stars
4.5
56
56
SAR 31.20
31.20


In [22]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [23]:
products_df = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df

pro_name            pro_rate  \
0   UGREEN iPhone Protective Case Compatible for i...  4.5 out of 5 stars   
1   Anker Powerline Micro USB - Charging Cable, wi...  4.3 out of 5 stars   
2   Anker Nano iPhone Charger, 20W PIQ 3.0 Durable...  4.2 out of 5 stars   
3   Moto G9 Power Smartphone ,20W Super Charge, 60...  4.0 out of 5 stars   
4   Wireless Earbuds, SOUNDPEATS S5 Over-Ear Hooks...  4.4 out of 5 stars   
5   Sony WF-1000XM4 Industry Leading Noise Cancell...  3.9 out of 5 stars   
6      Apple iPhone 12 With FaceTime (128GB) - Purple  4.4 out of 5 stars   
7   Compatible with Apple Watch Case Series 4 Seri...  3.9 out of 5 stars   
8       Apple iPhone 12 With FaceTime (128GB) - Black  4.4 out of 5 stars   
9   SoundPEATS Smart Watch New Upgraded 13 Sports ...  4.2 out of 5 stars   
10  SanDisk Ultra Micro SD Card Android - Class 10...  4.4 out of 5 stars   
11  UGREEN Fast Car Charger Adapter 42.5W Dual USB...  4.3 out of 5 stars   
12  ELON Fast Charging Cable for iPhone USB to Lig...  4.3 out of 5 stars   
13  UGREEN PD 20W Car Charger Fast Charging for iP...  4.3 out of 5 stars   
14  ibsun Wireless Charger, 3 in 1 Wireless Chargi...  4.1 out of 5 stars   
15  Samsung Galaxy S20 FE Dual SIM - 128GB, 8GB RA...  4.1 out of 5 stars   
16                                  Apple AirPods Pro  4.3 out of 5 stars   
17  UGREEN Magnetic Car Phone Holder Air Vent Moun...  4.0 out of 5 stars   
18  UGREEN Car Phone Mount Dashboard Car Holder Wi...  4.4 out of 5 stars   
19  New Apple iPhone 13 Pro Max with FaceTime (128...  4.5 out of 5 stars   
20  UGREEN iPhone 13 Charger Cable [MFi Certified]...  4.1 out of 5 stars   
21  HUAWEI FreeBuds 4i Wireless In-Ear Bluetooth E...  4.1 out of 5 stars   
22  UGREEN iPhone Charger PD20W USB C iPhone 13 Fa...  4.2 out of 5 stars   
23  SAMSUNG Galaxy Buds Pro, True Wireless Earbuds...  4.2 out of 5 stars   
24  JBL CLIP4 WIRELESS PORTABLE SPEAKER - Blue/Pin...  4.7 out of 5 stars   
25        SanDisk Extreme microSDXC UHS-I Card- 128GB  4.4 out of 5 stars   
26  Anker USB C Charger, 20W PIQ 3.0 Fast Charger ...  4.2 out of 5 stars   
27  HUAWEI HW-TIA-B09-BLACK WATCH FIT Smartwatch w...  4.5 out of 5 stars   
28  Samsung EP-TA800 Travel Adapter for Super Fast...  4.4 out of 5 stars   
29  ELONNIX PD 20W USB A + C Charger Type C Fast C...  4.3 out of 5 stars   
30  JBL T110 Wired Universal In-Ear Headphone with...  4.2 out of 5 stars   
31  Wireless Earbuds SoundPEATS TrueAir2 Bluetooth...  3.8 out of 5 stars   
32  Bose QuietComfort Earbuds - True Wireless Nois...  4.4 out of 5 stars   
33  Bose Noise Cancelling Wireless Bluetooth Headp...  4.5 out of 5 stars   
34      Apple iPhone 11 with FaceTime (128GB) - Black  4.3 out of 5 stars   
35  Hybrid Active Noise Cancelling Headphones with...  4.8 out of 5 stars   
36  Long ARM Black Color Flexible Clip Lazy Bed De...  3.4 out of 5 stars   
37    Apple Lightning to 3.5mm Headphone Jack Adapter  4.2 out of 5 stars   
38         Anker Powerline+ II 6 Foot Lightning Cable  3.9 out of 5 stars   
39  OWEMKIT Multifunctional Phone Holder Universal...  1.0 out of 5 stars   
40  New Apple iPhone 13 Pro Max with FaceTime (256...  4.5 out of 5 stars   
41  Belkin USB-C to Lightning Cable (iPhone Fast C...  4.5 out of 5 stars   
42  UGREEN 65W USB C PD Charger, GaN Charger Dual ...  4.4 out of 5 stars   
43  Samsung Galaxy A02 Dual SIM Smartphone - 32GB,...  3.7 out of 5 stars   
44  Stylus Pen for iPad with Palm Rejection，Active...  2.7 out of 5 stars   
45  UGREEN iPhone Lightning Cable 2M [MFi Certifie...  4.6 out of 5 stars   
46  Power Bank Portable Charger 10000mAh with cabl...  4.0 out of 5 stars   
47  UGREEN USB C Cable 3A Fast Charging Cable Nylo...  4.2 out of 5 stars   
48  Fasgear USB C Cable for Oculus Quest Link 2, 9...  4.0 out of 5 stars   
49  Stylus Pen for Touch Screens and Phone, Rechar...  3.8 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.5         56           

# Best Sellers in Wearable Technology (Page 1)

In [7]:
url= "https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966397031/ref=zg_bs_pg_1?ie=UTF8&pg=1"

In [8]:
response = requests.get(url)
response.status_code

200

In [9]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [10]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [11]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [12]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.6 out of 5 stars\n'

In [13]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [14]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Apple Watch Series 6 (GPS, 44mm) - Space Grey Aluminium Case with Black Sport Band
4.6 out of 5 stars
4.6
306
306
SAR 1,349.00
1349.00


In [15]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [16]:
products_df = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df

pro_name            pro_rate  \
0   Apple Watch Series 6 (GPS, 44mm) - Space Grey ...  4.6 out of 5 stars   
1   Apple Watch Series 6 (GPS, 40mm) - Gold Alumin...  4.6 out of 5 stars   
2   HUAWEI Band 6, All-day SpO2 Monitoring, 1.47" ...  4.4 out of 5 stars   
3   Apple Watch Series 6 (GPS, 40mm) - Blue Alumin...  4.6 out of 5 stars   
4   Apple Watch Series 6 (GPS, 40mm) - Space Grey ...  4.6 out of 5 stars   
5   Compatible with Apple Watch Case Series 4 Seri...  3.9 out of 5 stars   
6   Apple Watch Series 6 (GPS, 44mm) - Blue Alumin...  4.6 out of 5 stars   
7   ibsun Wireless Charger, 3 in 1 Wireless Chargi...  4.1 out of 5 stars   
8                       Fitbit-Inspire 2, Black/Black  4.5 out of 5 stars   
9   Milanese Loop Bracelet Stainless Steel band Fo...  4.3 out of 5 stars   
10  HUAWEI HW-TIA-B09-BLACK WATCH FIT Smartwatch w...  4.5 out of 5 stars   
11  Smart Watch, YCCORG Fitness Tracker with Heart...  3.8 out of 5 stars   
12  SoundPEATS Smart Watch New Upgraded 13 Sports ...  4.2 out of 5 stars   
13  Xiaomi Mi Band 4 Smart Bluetooth Fitness Brace...  4.4 out of 5 stars   
14  Samsung Galaxy Watch3 Stainless BT 45mm, Black...  4.3 out of 5 stars   
15  Xiaomi Band 5 Smart Fitness Bracelet Heart Rat...  4.5 out of 5 stars   
16  Apple Watch Series 7 (GPS, 41mm) - Midnight Al...  5.0 out of 5 stars   
17  24HOCL Smart Watch for Kids Girls Boys, Activi...  5.0 out of 5 stars   
18                     Fitbit Charge 5,Graphite/Black  3.1 out of 5 stars   
19  Apple Watch Series 7 (GPS, 45mm) - Midnight Al...  4.6 out of 5 stars   
20  SKULLCANDY Dime True Wireless In-Ear Earbuds W...  4.1 out of 5 stars   
21  Huawei Watch GT 2 Pro Glass Screen Protector, ...  3.0 out of 5 stars   
22  Fitbit Sense, Advanced Smartwatch with Tools f...  4.3 out of 5 stars   
23  Apple Watch Series 7 (GPS + Cellular, 45mm) - ...  5.0 out of 5 stars   
24  Apple Watch Series 7 (GPS, 41mm) - Starlight A...  5.0 out of 5 stars   
25  SKULLCANDY Dime True Wireless In-Ear Earbuds W...  4.1 out of 5 stars   
26  hw22 plus Smart Watch series 6 Bluetooth Call ...  2.4 out of 5 stars   
27  Fitbit Sense, Advanced Smartwatch with Tools f...  4.3 out of 5 stars   
28  Screen Protector Compatible with Huawei Watch ...  3.2 out of 5 stars   
29  MAZTRON 6-Pack Silicone Band Compatible with A...  4.4 out of 5 stars   
30  Samsung Galaxy Watch Active 2 , 40 mm Aluminiu...  5.0 out of 5 stars   
31  INFOSUN Compatible with Apple Watch Bands 42mm...  3.5 out of 5 stars   
32  Apple Watch Series 6 (GPS, 40mm) - Silver Alum...  4.6 out of 5 stars   
33  w26 plus smart watch w26 smart watch w26 smart...  3.1 out of 5 stars   
34  Smart Watch for Women, AGPTEK 1.69"(43mm) Smar...  3.7 out of 5 stars   
35  Case for Apple Watch 7 45mm Soft Slim TPU All ...  3.0 out of 5 stars   
36  Fitbit Ace 3, Activity Tracker for Kids 6+ wit...  4.4 out of 5 stars   
37  INFOSUN Compatible with Apple Watch Bands 38mm...  3.5 out of 5 stars   
38  Fitbit Sense, Advanced Smartwatch with Tools f...  4.3 out of 5 stars   
39  Xiaomi Mi Smart Watch Lite Black- 1.4 Inch Tou...  4.2 out of 5 stars   
40  Fitbit Versa 3, Health & Fitness Smartwatch wi...  4.4 out of 5 stars   
41                        Charge 4 (NFC), Black/Black  4.4 out of 5 stars   
42  Smart Watch for Men Women (Receive/Make Call)1...  1.8 out of 5 stars   
43  w34 Bluetooth Smart Watch W34 Series 4 5 ECG H...  3.4 out of 5 stars   
44  INFOSUN Compatible with Apple Watch Bands 38mm...  3.5 out of 5 stars   
45          Apple Watch Magnetic Charging Cable (1 m)  3.0 out of 5 stars   
46        Apple AirTag Leather Key Ring - Baltic Blue                 NaN   
47  Apple Watch SE (GPS, 44mm) - Silver Aluminium ...  4.4 out of 5 stars   
48  Compatible with Apple Watch Band 40mm 38mm, Ad...  3.8 out of 5 stars   
49  Smart Watch, Yccorg 1.54-inch Fitness Tracker ...  3.5 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.6        306           

# Best Sellers in Wearable Technology (Page 2)

In [17]:
url = "https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966397031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [18]:
response = requests.get(url)
response.status_code

200

In [19]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [20]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [21]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [22]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n3.6 out of 5 stars\n'

In [23]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [24]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

INFOSUN Compatible with Apple Watch Bands 42mm/44mm/45mm Women Men,Braided Solo Loop Replacement Band Strap Stretchable Elastic Sport Wristbandfor Series 7/6/SE/5/4/3/2/1 (42mm/44mm/45mm-L, Black)
3.5 out of 5 stars
3.5
33
33
SAR 37.13
37.13


In [25]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [26]:
products_df = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df

pro_name            pro_rate  \
0   INFOSUN Compatible with Apple Watch Bands 42mm...  3.5 out of 5 stars   
1   Smart Watch, AGPTEK 1.69"(43mm) Smartwatch for...  3.6 out of 5 stars   
2   Compatible with HUAWEI Samsung Watch Silicone ...  3.7 out of 5 stars   
3   6 Pack Sport Bands Compatible with Apple Watch...                 NaN   
4   Rekletier Replacement Bands Compatible with Fi...                 NaN   
5   GEEAN Stainless Steel Watch Band for Apple Wat...  3.7 out of 5 stars   
6   Apple Watch Series 7 (GPS, 45mm) - Blue Alumin...                 NaN   
7   OMIRA Smart Watch, Fitness Tracker with Heart ...  3.8 out of 5 stars   
8   Compatible with Apple Watch Bands 44mm 42mm, A...  3.8 out of 5 stars   
9   Replacement Bands Compatible for Fitbit Charge...  2.5 out of 5 stars   
10  Apple Watch Series 7 (GPS + Cellular, 45mm) - ...                 NaN   
11  Apple Watch Series 6 (GPS + Cellular, 40mm) - ...  4.2 out of 5 stars   
12  Compatible with Apple Watch Band 45mm 44mm 42m...  2.8 out of 5 stars   
13  Xioami Mi Smart Band 6 Sports Smart Bracelet- ...  4.3 out of 5 stars   
14  VR Box VR02 Virtual Reality 3D Glasses with Bl...  2.3 out of 5 stars   
15  Compatible with Apple Watch band 44mm, Watch S...  3.4 out of 5 stars   
16  HW22 PRO MAX Smart watch 1.78 Inch IPS Color S...  3.5 out of 5 stars   
17  INFOSUN Compatible with Apple Watch Bands 42mm...  3.5 out of 5 stars   
18  MyHarem Replacement Bands Compatible For Huawe...  4.1 out of 5 stars   
19  HONOR Band 6, Model ARG-B39, 1.47" AMOLED Disp...  4.1 out of 5 stars   
20  Fitbit Versa 3,Soft Gold/Thistle, Small and La...  4.4 out of 5 stars   
21  Ametoys P20 1.4'' Full Touch Smart Watch,Multi...  2.3 out of 5 stars   
22  Huawei Honor Band 5 Charger Cable & uawei Band...  4.2 out of 5 stars   
23  Smárt Watches - HW22 Plus Smárt Watch Women 1....  4.1 out of 5 stars   
24  Smart Watch,Fitness Watch Cardio Exercise Hear...  3.5 out of 5 stars   
25  HUAWEI WATCH GT 2 Pro Smartwatch, 1.39" AMOLED...  4.4 out of 5 stars   
26  24HOCL Smart Watch with 1.69'' Full Touch Scre...  4.1 out of 5 stars   
27  INFOSUN Compatible with Apple Watch Bands 38mm...  3.5 out of 5 stars   
28  INFOSUN Compatible with Apple Watch Bands 42mm...  3.5 out of 5 stars   
29  GEEAN Silicone Watch Band Sport Watch Strap fo...  3.7 out of 5 stars   
30  Compatible with HUAWEI Samsung Watch Silicone ...  3.7 out of 5 stars   
31  INFOSUN Compatible with Apple Watch Bands 38mm...  3.5 out of 5 stars   
32  MAZTRON 6-Pack Silicone Band Compatible with A...  4.4 out of 5 stars   
33  Smárt Watches - HW22 Plus Smárt Watch Women 1....  4.1 out of 5 stars   
34  Smart Watch, AGPTEK Smartwatch for Men Women I...  3.7 out of 5 stars   
35  Compatible with Apple Watch Band, Nylon Strap ...  5.0 out of 5 stars   
36  Compatible with HUAWEI Samsung Watch Soft Sili...  3.3 out of 5 stars   
37  INFOSUN Compatible with Apple Watch Bands 38mm...  3.5 out of 5 stars   
38  HW22 PRO MAX MYK Smart watch 1.78LTPS full Scr...                 NaN   
39  Compatible for Samsung Galaxy Watch 3 45mm Ban...                 NaN   
40  Watch Straps Compatible for HUAWEI Watch Fit, ...  4.4 out of 5 stars   
41  ONMROAD Compatible for Apple Watch Case 44mm w...  4.3 out of 5 stars   
42  INFOSUN Compatible with Apple Watch Bands 38mm...  3.5 out of 5 stars   
43  12 Pack Case Compatible for Apple Watch 44mm S...  4.5 out of 5 stars   
44  INFOSUN Compatible with Apple Watch Bands 38mm...  3.5 out of 5 stars   
45  INFOSUN Compatible with Apple Watch Bands 38mm...  3.5 out of 5 stars   
46  Smart Watch, Necomi ساعة ذكية, Fitness Tracker...  4.5 out of 5 stars   
47  [2-Pack] Hard Case for Apple Watch Series 6 / ...  4.2 out of 5 stars   
48  Compatible Apple Watch Case 40mm with Screen P...  3.7 out of 5 stars   
49  Matte Case for Apple Watch 7 41mm 45mm, Hard P...  5.0 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             3.5         33           

# Best Sellers in Car & Vehicle Electronics (Page 1)

In [27]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966386031/ref=zg_bs_nav_1_electronics"

In [28]:
response = requests.get(url)
response.status_code

200

In [29]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [30]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [31]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [32]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.3 out of 5 stars\n'

In [33]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [34]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

UGREEN Bluetooth Aux Adapter, Bluetooth 5.0 Audio Receiver for Wireless Music Stream with Hand-free Call, aptX LL, 10H Play Time, Auto-Repair for Car Speaker, Headphone, Audio Sound System, etc
4.5 out of 5 stars
4.5
218
218
SAR 93.60
93.60


In [35]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [36]:
products_df = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df

pro_name            pro_rate  \
0   UGREEN Bluetooth Aux Adapter, Bluetooth 5.0 Au...  4.5 out of 5 stars   
1   UGREEN Fast Car Charger Adapter 42.5W Dual USB...  4.3 out of 5 stars   
2   UGREEN PD 20W Car Charger Fast Charging for iP...  4.3 out of 5 stars   
3   UGREEN Car Phone Mount Dashboard Car Holder Wi...  4.4 out of 5 stars   
4   Anker Power Drive 2 24W 2 Port Car Charger For...  4.2 out of 5 stars   
5   Magnetic Phone Car Mount, WORLDMOM Strong Magn...                 NaN   
6   UGREEN Magnetic Car Phone Holder Air Vent Moun...  4.0 out of 5 stars   
7   UGREEN Car Phone Holder Magnetic Dashboard Mob...  4.2 out of 5 stars   
8   Muson Car Phone Mount, Dashboard/Air Vent/Wind...  3.7 out of 5 stars   
9   UGREEN Car Air Vent Mount Cell Phone Holder Gr...  4.4 out of 5 stars   
10  UGREEN Bluetooth 5.0 Adapter Car Bluetooth V5....  4.2 out of 5 stars   
11  UGREEN Bluetooth Receiver for Car, Portable Wi...  4.0 out of 5 stars   
12  AccLoo Wireless Car Charger, 15W Qi Fast Charg...  5.0 out of 5 stars   
13  UGREEN Car Phone Holder Air Vent Cell Phone Mo...  4.3 out of 5 stars   
14  UGREEN Car Phone Mount CD Slot Holder Gravity ...  4.0 out of 5 stars   
15  UGREEN Bluetooth FM Transmitter USB Car Fast C...  3.7 out of 5 stars   
16                        ANKER POWERDRIVE 2 QC BLACK  3.9 out of 5 stars   
17  UGREEN Fast Car Charger Set with USB C Cable Q...  4.4 out of 5 stars   
18  UGREEN Dashboard Car Phone Clip Holder Dash HU...  3.9 out of 5 stars   
19  UGREEN Car Air Vent Mount Cell Phone Holder Gr...  4.4 out of 5 stars   
20  70mai A500S Pro Plus+, 2K Front and Interior, ...                 NaN   
21  Baseus 360-degree Rotation Magnetic Mount Hold...  3.8 out of 5 stars   
22  Promate Magnetic Car Mount Holder, Flexible Go...  4.5 out of 5 stars   
23  AccLoo Bluetooth FM Transmitter for Car,Blueto...  5.0 out of 5 stars   
24  UGREEN Fast Car Charger PD 40W Dual USB C Port...  4.3 out of 5 stars   
25  UGREEN Magnetic Car Mount Dashboard Cell Phone...  4.1 out of 5 stars   
26  UGREEN Bluetooth Aux Adapter Bluetooth Car Rec...  4.4 out of 5 stars   
27  UGREEN Fast Car Charger 36W Dual USB QC 3.0 Qu...  4.3 out of 5 stars   
28  15W Qi Wireless Fast Car Mount Charger, Auto D...  4.5 out of 5 stars   
29  Belkin USB-C PD Car Charger 36W (Dual 18W USB-...  4.6 out of 5 stars   
30          Belkin Magnetic Car Vent Mount V2 MagSafe  3.7 out of 5 stars   
31  Universal Smartphone Car Phone Holder Mount Cl...  3.0 out of 5 stars   
32  Huawei CP37 Type-C Car Charger with Super Char...  4.7 out of 5 stars   
33  Baseus Small Ears Series Magnetic Bracket（Vert...  4.4 out of 5 stars   
34  Yesido magic Glue Silicone Wall Cell Phone Sta...  4.8 out of 5 stars   
35  Universal Adjustable Car Mount Stand for Smart...  3.8 out of 5 stars   
36  Tekpatt Car Phone Holder, Universal Air Vent C...  5.0 out of 5 stars   
37  Go-Des Mini Strip Car Mount, Universal Mobile ...  4.5 out of 5 stars   
38  UGREEN Mini Car Charger Quick Charge 24W Dual ...  4.5 out of 5 stars   
39  Car Phone Mount, Air Vent Cell Phone Holder fo...  4.1 out of 5 stars   
40  UGREEN Bike Phone Holder, Bicycle Motorcycle P...  4.3 out of 5 stars   
41  Ford Dedicated Cover Key Fob Case Suit For Key...                 NaN   
42  UGREEN Car Headrest Mount Car Phone Mount Mobi...  4.2 out of 5 stars   
43  - Functional Mobile Phone Holder/Mount/Clip/Bu...  3.5 out of 5 stars   
44  SAMSUNG Super Fast Dual Car Charger (45W+15W) ...  4.7 out of 5 stars   
45  اكس ام مشغل DVD شاشة لسقف السيارة مقاس 8.5 بوص...                 NaN   
46  LED Strip Light, 2M 5050 RGB Waterproof Lights...  3.2 out of 5 stars   
47  Charger for Apple Watch, Travel Car Charger, P...  4.5 out of 5 stars   
48  GUB Bicycle & Motorcycle Phone Mount, Aluminum...  4.4 out of 5 stars   
49  4 Types 12V Add-a-Circuit Adapter & Fuse Kit -...  5.0 out of 5 stars   

   pro_rate_clean review_num review_num_clean   pro_price pro_price_clean  
0             4.5        218             

# Best Sellers in Car & Vehicle Electronics (Page 2)

In [37]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966386031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [38]:
response = requests.get(url)
response.status_code

200

In [39]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [40]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [41]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [42]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.5 out of 5 stars\n'

In [43]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [44]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Hide Car Charger for Routers 1.5 Meter Pin: 2.5
2.9 out of 5 stars
2.9
8
8




In [45]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [46]:
products_df = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df

pro_name            pro_rate  \
0     Hide Car Charger for Routers 1.5 Meter Pin: 2.5  2.9 out of 5 stars   
1   Tekpatt Gravity Car Phone Holder, Universal Ai...  4.5 out of 5 stars   
2   Universal Dashboard Car Mount Holder Rearview ...  3.0 out of 5 stars   
3   Tekpatt Car Phone Holder, Universal Air Vent C...  3.5 out of 5 stars   
4   Decdeal 95pcs 5050 RGB LED-Strip Connector Kit...                 NaN   
5   LE LED Strip Lights for TV, 6.56Ft RGB Color C...  3.4 out of 5 stars   
6          AMH Universal Magnetic Mobile Phone Holder  3.5 out of 5 stars   
7   Car Phone Mount, PHOCAR Universal Phone Holder...  2.8 out of 5 stars   
8   Anker Mini 24W 4.8A Metal Dual USB Car Charger...                 NaN   
9   GoolRC 700W Adjustable Speed Car Waxing Polish...  1.0 out of 5 stars   
10  Decdeal Car Megaphone 5 Tone Alarm Horn 12V 11...                 NaN   
11  UGREEN Car Phone Holder for CD Slot Auto Lock ...  4.1 out of 5 stars   
12  Powerology Wireless Charger Car Mount, Phone H...                 NaN   
13  2-Way In-Wall In-Ceiling Speaker System - Dual...  4.5 out of 5 stars   
14  Low-Profile Waterproof Marine Speakers - 240W ...  4.4 out of 5 stars   
15    Duracell Car Charger Single USB White - DR5020W  5.0 out of 5 stars   
16  Bluetooth V2.0 7 Inch 2 DIN Car Video Stereo P...  3.1 out of 5 stars   
17  Car Phone Mount, Universal Air Vent Car Smartp...  4.0 out of 5 stars   
18  Anker 24W Dual USB Car Charger, PowerDrive 2 f...                 NaN   
19  iOttie Easy One Touch 5 Air Vent Car Mount Pho...  4.4 out of 5 stars   
20  Ozgoe Happy Bell (12 Pack) Mini Mount Metal Pl...  4.4 out of 5 stars   
21  EZCase Air Vent Magnetic Car Mount Matte Finis...  4.4 out of 5 stars   
22  Baseus T typed S-09 Bluetooth MP3 car charger ...  2.0 out of 5 stars   
23  SMAPRO Car and Desktop Phone Holder, Car Mount...  3.2 out of 5 stars   
24  Eacam Wireless Car Charger Mount, 10W Fast Cha...                 NaN   
25  Urise Car Phone Holder, 360° adjustable cup mo...  3.3 out of 5 stars   
26  iOttie Easy One Touch 5 Dashboard & Windshield...  4.4 out of 5 stars   
27  Belkin Car Universal Mount (Car Mount for iPho...  4.4 out of 5 stars   
28  Car Phone Holder Gravity Air Vent Car Phone Mo...  3.5 out of 5 stars   
29  TLAXCA Wireless Car Charger, Intelligent Auto ...  5.0 out of 5 stars   
30  Bluetooth 5.0 Transmitter 2 in 1 Bluetooth Rec...  5.0 out of 5 stars   
31  LENCENT FM Transmitter, Bluetooth FM Transmitt...  4.4 out of 5 stars   
32  UGREEN Car Phone holder Car air Vent Gravity L...  4.0 out of 5 stars   
33  UGREEN Car Phone Mount Dashboard Clip Cell Pho...  3.4 out of 5 stars   
34  Magnetic mobile holder - 360 dgree Rotation - ...  3.0 out of 5 stars   
35  Air Vent Phone Holder for Car, Universal Vehic...  5.0 out of 5 stars   
36  UGREEN Dashboard Phone Holder 360 Degree Car P...  3.6 out of 5 stars   
37  Mobile Phone Holder for Car Mount, Durable Das...  4.3 out of 5 stars   
38  UGREEN Magnetic Car Mount Phone Holder Univers...  4.2 out of 5 stars   
39  Universal Bluetooth Aux Music Receiver 3.5mm S...  2.4 out of 5 stars   
40  Car Headrest Mount Tablet Holder，ShowTop Unive...  4.0 out of 5 stars   
41  360 Universal Flexible Lazy Bed Desktop Car St...  3.2 out of 5 stars   
42  UGREEN Bluetooth 5.0 Audio Transceiver Wireles...  3.8 out of 5 stars   
43                                       WithElephant  2.8 out of 5 stars   
44              10pc Automotive Fuses Kit with Tester                 NaN   
45  2 Replacement Keyless Entry Remote Control Key...                 NaN   
46  Automatic Clamping 15W Fast Car Wireless Charg...  5.0 out of 5 stars   
47  120W USB C Car Fast Charger - Dual Ports PPS P...  3.0 out of 5 stars   
48  Green Desert Car CD holder mobile phone holder...  1.9 out of 5 stars   
49  WUW for MagSafe Car Mount Charger Stand Holder...                 NaN   

   pro_rate_clean review_num review_num_clean   pro_price pro_price_clean  
0             2.9          8             

# Best Sellers in Electrical Power Accessories (Page 1)

In [47]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966395031/ref=zg_bs_nav_1_electronics"

In [48]:
response = requests.get(url)
response.status_code

200

In [49]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [50]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [51]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [52]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n3.9 out of 5 stars\n'

In [53]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [54]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Apple 20W USB-C Power Adapter, White
4.5 out of 5 stars
4.5
359
359
SAR 79.00
79.00


In [55]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [56]:
products_df = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df

pro_name            pro_rate  \
0                Apple 20W USB-C Power Adapter, White  4.5 out of 5 stars   
1   Extension Cord with 3 Power Socket and 3 USB S...  3.9 out of 5 stars   
2   LDNIO SC3604 Socket extension, 6USB Ports 3.4A...  3.9 out of 5 stars   
3   Multi Extension Socket Plug Adapter with 3 USB...  4.6 out of 5 stars   
4   Universal AU US EU to UK AC Power Plug Travel ...  3.6 out of 5 stars   
5   FLIZIL Fast Charging Universal Travel Adapter,...  4.5 out of 5 stars   
6   Travel Adapter for KSA/UAE/UK, Plug for US/EU/...  4.4 out of 5 stars   
7   FLIZIL USB C Cable 3A Fast Charging Cable Nylo...  4.5 out of 5 stars   
8   Belkin BSV804ar2M 8-Outlet Surge Protection Ex...  4.5 out of 5 stars   
9   FLIZIL Lightning Cable, Apple MFi Certified Li...  4.5 out of 5 stars   
10  Double Socket Adapter with USB, 5V 2.1A USB Wa...  5.0 out of 5 stars   
11                  Power connection with 6 USB ports  3.3 out of 5 stars   
12             Terminator 3 Way Universal Plug Socket  4.1 out of 5 stars   
13  Lawazim 2-Socket Extension Strip with 5 Meters...  3.7 out of 5 stars   
14  3-Socket Extension Cord with Individual on/off...  3.8 out of 5 stars   
15  FLIZIL Power Strip Extension with 4 way Socket...  4.5 out of 5 stars   
16  Multi Plug Extension Sockets ，3 Way Multi Plug...                 NaN   
17              Enriches electricity with 6 USB Ports  4.4 out of 5 stars   
18  3-Socket Extension Cord with Individual on/off...  3.8 out of 5 stars   
19  Travel Adaptor for KSA/US/UK/JP/CN/AU Plug Con...  3.2 out of 5 stars   
20  Anself Intelligent Efficient Household 200W AC...  2.6 out of 5 stars   
21  US/CA/JP Type B Adaptor Plug with Flat Blades/...  3.4 out of 5 stars   
22  Belkin BSV400ar2M 4 Way/4 Plug 2 m Surge Prote...  4.5 out of 5 stars   
23  LDNIO 4 Power Socket Extension 4 USB (18w) Def...  4.6 out of 5 stars   
24  5.6A Fast Charging Worldwide Travel Adapter Pl...  4.6 out of 5 stars   
25  Belkin BSV603ar2M 6 Way/6 Plug 2m Surge Protec...  4.5 out of 5 stars   
26  LDNIO POWERFUL CHARGING SERISE Power Strip wit...  3.7 out of 5 stars   
27  Socket extension, 6USB Ports with on/off Switc...  3.0 out of 5 stars   
28  LDNIO SC3412 Socket extension, 3USB Ports,Type...                 NaN   
29  BXOE - Extension Lead Tower 12 Way, Power Stri...  5.0 out of 5 stars   
30  Belkin BSV804 8 Way 2m Surge Protection Extens...  3.3 out of 5 stars   
31  فيش كهرباء Universal AU US EU to UK AC POWER P...  2.1 out of 5 stars   
32  TOMSHOO Universal Travel Adapter 4 USB 2.4A Ch...  2.9 out of 5 stars   
33  PEGANT 4 Way 3M Power Extension Cord 4 Univers...  4.9 out of 5 stars   
34  YUNSYE White UK 2 Pin To 3 Pin 1A Fuse Adaptor...  3.7 out of 5 stars   
35  Universal Power Adapter AC 100-240V DC 12V 2A ...  3.3 out of 5 stars   
36  2 Pcs/Set Universal AC Power Plugs US To EU To...  3.6 out of 5 stars   
37  Smart Power strip, Power extension 4 Way, 2 Qu...  3.8 out of 5 stars   
38                          Socket Adapter 3 Way 7012  4.1 out of 5 stars   
39  KLARHEIT Upgraded Universal Travel Adapter One...  3.9 out of 5 stars   
40             4 Way Universal T-Socket Multi Adaptor  4.4 out of 5 stars   
41  Wall Mounted USB Power Strip, NTONPOWER Multi ...  4.2 out of 5 stars   
42  [2-Pack]US USA America/ Canada/ EU Europe Euro...                 NaN   
43  Key Power 200-Watt Step Down 220V to 110V Volt...  4.4 out of 5 stars   
44  LENCENT 2X EU to UK Plug Adapter, Europe Schuk...  5.0 out of 5 stars   
45  UK to EU AC Power Adapter Plug Adapter - Trave...  3.4 out of 5 stars   
46  Extension Power Cord Multi Plug Vertical Tower...  5.0 out of 5 stars   
47  Travel Adapter for KSA/UAE/UK, Plug for US/EU/...  4.4 out of 5 stars   
48  Smart Power Strip Wi-Fi Smart Plug Socket Powe...  4.4 out of 5 stars   
49  Promate Power Strip with USB-C Port, 10-in-1 S...                 NaN   

   pro_rate_clean review_num review_num_clean   pro_price pro_price_clean  
0             4.5        359             

# Best Sellers in Electrical Power Accessories (Page 2)

In [57]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966395031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [58]:
response = requests.get(url)
response.status_code

200

In [59]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [60]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [61]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [62]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n3.7 out of 5 stars\n'

In [63]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [64]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

Power connection of 2500 watts multi-use
4.0 out of 5 stars
4.0
35
35
SAR 85.60
85.60


In [65]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [66]:
products_df = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df

pro_name            pro_rate  \
0            Power connection of 2500 watts multi-use  4.0 out of 5 stars   
1   2-Socket Extension Cord with on/off Switch wit...  3.7 out of 5 stars   
2           Extension Cord, 5 Meters, 4 Ports, German  4.9 out of 5 stars   
3   Extension Cord 4 Way Power Strip White Extensi...  4.6 out of 5 stars   
4   Narken E-Series Electric Universal Extension C...                 NaN   
5   Philips 5 Way Heavy duty Indivisual Switch Soc...  5.0 out of 5 stars   
6   Haylink CE ROHS سبائك الألومنيوم المشبك سطح ال...                 NaN   
7   LENCENT 2Pcs UK to EU Euro Europe Plug Adapter...                 NaN   
8   Mark 3864 High Quality Power socket Extension 10m  2.6 out of 5 stars   
9   Black Extension Lead 4way Power Socket 1.8m Ex...  5.0 out of 5 stars   
10                  Power Socket Extension Board Cord                 NaN   
11  Universal Vertical Extension Cord Lead Tower S...  4.4 out of 5 stars   
12  Universal Travel Adapter, NTONPOWER Worldwide ...                 NaN   
13  HOOPO-Power Strip with 6 USB 3 Power Socket 5....  5.0 out of 5 stars   
14  Electrical Socket 4 Way Power Strip 3m Extensi...  4.7 out of 5 stars   
15  BS 8546 Approved South African Large Plug Type...                 NaN   
16  Universal US Plug Adapter, Power Plug Travel C...                 NaN   
17  HWEN-JP Smart Power Extension WiFi Plug Surge ...                 NaN   
18  KSA/UAE/UK to US/Canada/Japan Plug Adaptor, 3-...  4.7 out of 5 stars   
19  Belkin BSV604ar2M 6 Way/ 6 Plug 2m Surge Prote...  4.5 out of 5 stars   
20  Narken TC E6-3 E-SeriesExtension Cord, 6 Ways ...  4.7 out of 5 stars   
21  Premium-Line 4-Way Extension Lead Power Strip ...                 NaN   
22  US/CA/JP Type B Adaptor Plug with Flat Blades/...  3.3 out of 5 stars   
23  Multi USB Wall Plug Adapter with 2 USB, TESSAN...                 NaN   
24  3 Meter Power Extension Cord, NTONPOWER 3250W ...  4.2 out of 5 stars   
25  YUNSYE Power Strips Extension Lead w 6 USB Wal...  3.7 out of 5 stars   
26  Belkin Surge Protector 6 Outlet 2 USB 2.4A - B...  3.8 out of 5 stars   
27  BS8546 Approved KSA/UAE/UK to EU/DE/FR Adaptor...  4.6 out of 5 stars   
28  Extension Lead 2 Sockets Power Strip 1.8m Exte...  4.0 out of 5 stars   
29  Australian/New Zealand to KSA/UAE/UK Plug Adap...  4.7 out of 5 stars   
30  [2-Pack]US USA America/ Canada/ EU Europe Euro...                 NaN   
31  LENCENT Universal Travel Adaptor with UK/USA/E...  5.0 out of 5 stars   
32  US/Canada/Japan to KSA/UAE/UK Plug Adaptor, US...  4.7 out of 5 stars   
33  Wall Mounted Power Strip with 3 Meter Extensio...  3.0 out of 5 stars   
34             TVON POWER SOCKET 5M W/2USB TN-U6603-5  3.7 out of 5 stars   
35  Vertical Power Strip 4 layers, 11 outlets with...  4.0 out of 5 stars   
36  3-Socket Extension Cord with Individual on/off...  3.8 out of 5 stars   
37  Wall Mounted Extension Lead, NTONPOWER USB Pow...  4.5 out of 5 stars   
38  ORINTED Power Socket Strip with 3 Outlets 2500...                 NaN   
39  Smart timer power strip with 3 AC outlets and ...  5.0 out of 5 stars   
40  Vertical Power Strip 3 layers,11outlets with 2...  3.8 out of 5 stars   
41                        Apple 12W USB Power Adapter  4.5 out of 5 stars   
42  LDNIO EU Plug 3 Port Power Strip USB Charger A...  3.4 out of 5 stars   
43  Extension Lead with Superior Surge Protection,...  4.2 out of 5 stars   
44  3 Meter Extension Cord, NTONPOWER 3250W Power ...  4.2 out of 5 stars   
45  Smart Design Solutions Electrical Extension Le...  4.8 out of 5 stars   
46  EVGA SuperNOVA 550 G3, 80+ GOLD, 550W Fully Mo...  4.7 out of 5 stars   
47  ELU6P5MBSW Electric Extension 6 Ports 5 meter ...  4.6 out of 5 stars   
48  Travel Adaptor for KSA/US/UK/JP/CN/AU Plug Con...  3.2 out of 5 stars   
49  HUACHEST Remote Control &Voice Control Smart p...  5.0 out of 5 stars   

   pro_rate_clean review_num review_num_clean   pro_price pro_price_clean  
0             4.0         35             

# Best Sellers in Computer Tablets (Page 1)

In [68]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966433031/ref=zg_bs_nav_1_electronics"

In [69]:
response = requests.get(url)
response.status_code

200

In [70]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [71]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [72]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [73]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n4.1 out of 5 stars\n'

In [74]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [75]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) - Space Grey (4th Generation)
4.4 out of 5 stars
4.4
157
157
SAR 2,449.00
2449.00


In [76]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [77]:
products_df = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df

pro_name            pro_rate  \
0   2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) -...  4.4 out of 5 stars   
1   Samsung Electronics A7 Tablet 10.4 Wi-Fi 64GB ...  4.1 out of 5 stars   
2   SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
3   2021 Apple 10.2-inch iPad (Wi-Fi, 64GB) - Spac...  4.2 out of 5 stars   
4   2021 Apple iPad Pro (11-inch, Wi-Fi, 128GB) - ...  4.6 out of 5 stars   
5   Lenovo Smart Tab M10 Plus, 10.3" Android Table...  4.2 out of 5 stars   
6   Samsung Galaxy Tab S7+ Wi-Fi, Mystic Black - 2...  4.7 out of 5 stars   
7   SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
8   2020 Apple iPad Air (10.9-inch, Wi-Fi, 256GB) ...  4.4 out of 5 stars   
9   SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
10  Samsung Galaxy Tab S7 Wi-Fi, Mystic Black - 512GB  4.7 out of 5 stars   
11  2021 Apple 10.2-inch iPad (Wi-Fi, 256GB) - Spa...  4.2 out of 5 stars   
12  Samsung Galaxy Tab S7+ Wi-Fi, Mystic Black - 5...  4.7 out of 5 stars   
13  Samsung Electronics Galaxy Tab S7 Wi-Fi, Mysti...  4.7 out of 5 stars   
14  Microsoft Surface Pro 7 Tablet - 12.3 Inch, 10...  4.6 out of 5 stars   
15  Samsung Galaxy Tab S7 Wi-Fi, Mystic Navy - 256 GB  4.7 out of 5 stars   
16  HUION HS64 Graphics Drawing Tablet with Batter...  4.4 out of 5 stars   
17  2021 Apple iPad Pro (12.9-inch, Wi-Fi, 128GB) ...  4.8 out of 5 stars   
18  SAMSUNG Galaxy Tab S7 11-inch Android Tablet 1...  4.7 out of 5 stars   
19  Huawei Matepad T10S, 10.1", WIFI, 32GB, Deepse...  3.1 out of 5 stars   
20    2021 Apple iPad mini (Wi-Fi, 64GB) - Space Grey  4.1 out of 5 stars   
21  Other 2724602275984 in 1 Precision Screwdriver...  4.2 out of 5 stars   
22  2021 Apple 10.2-inch iPad (Wi-Fi + Cellular, 6...  4.2 out of 5 stars   
23  Microsoft Surface GO 2 [STV-00005], Tablet-PC,...  4.5 out of 5 stars   
24  Samsung Electronics Galaxy Tab S7+ Wi-Fi, Myst...  4.7 out of 5 stars   
25  Microsoft Surface Pro 7 Tablet - 12.3 Inch, 10...  4.5 out of 5 stars   
26  2021 Apple 10.2-inch iPad (Wi-Fi + Cellular, 2...  4.2 out of 5 stars   
27   2021 Apple iPad mini (Wi-Fi, 256GB) - Space Grey  4.1 out of 5 stars   
28  Tablet, GoolRC 10.1'' Metal Tablet with MT6592...                 NaN   
29  2021 Apple iPad Pro (11-inch, Wi-Fi + Cellular...  4.6 out of 5 stars   
30  2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) -...  4.4 out of 5 stars   
31  Lenovo Tab M8 HD 2ND GEN (TB-8505F), 8 inch Ta...  3.8 out of 5 stars   
32  SAMSUNG Galaxy Tab S7+ Plus 12.4-inch Android ...  4.7 out of 5 stars   
33  2021 Apple 10.2-inch iPad (Wi-Fi + Cellular, 6...  4.2 out of 5 stars   
34  Microsoft Surface Go 2 Tablet STQ-00005, Intel...  4.2 out of 5 stars   
35  Xiaomi Pad 5 11" Tablet, 128GB, 6GB RAM, Wi-Fi...                 NaN   
36  Samsung Galaxy Tab S6 Lite, 64GB, 4GB RAM, Wi-...  4.3 out of 5 stars   
37  SAMSUNG Galaxy Tab S7 Wi-Fi, Mystic Silver - 2...  4.7 out of 5 stars   
38  2021 Apple iPad Pro (11-inch, Wi-Fi + Cellular...  4.6 out of 5 stars   
39  Microsoft Surface Pro 7 Tablet - 12.3 Inch, 10...  3.4 out of 5 stars   
40   2021 Apple 10.2-inch iPad (Wi-Fi, 64GB) - Silver  4.2 out of 5 stars   
41  2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) -...  4.4 out of 5 stars   
42  2021 Apple iPad Pro (11-inch, Wi-Fi, 256GB) - ...  4.6 out of 5 stars   
43  Apple iPad Pro (12.9-inch, Wi-Fi, 256GB) - Silver  4.3 out of 5 stars   
44  2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) -...  4.4 out of 5 stars   
45  2021 Apple iPad Pro (12.9-inch, Wi-Fi, 128GB) ...  4.8 out of 5 stars   
46  Samsung Electronics Tab A7 Lite 8.7" Gray 32GB...  3.5 out of 5 stars   
47  2020 Apple iPad Air (10.9-inch, Wi-Fi, 64GB) -...  4.4 out of 5 stars   
48  Tablet 10.1 inch System 8.1 Tablet PC, 6GB RAM...                 NaN   
49  2 in 1 Android 10.0 Tablet 10 Inch 5G WiFi Tab...  3.8 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.4        157           

# Best Sellers in Computer Tablets (Page 2)

In [78]:
url="https://www.amazon.sa/-/en/gp/bestsellers/electronics/16966433031/ref=zg_bs_pg_2?ie=UTF8&pg=2"

In [79]:
response = requests.get(url)
response.status_code

200

In [80]:
response.text[:1000]

'<!doctype html><html lang="en-ae" class="a-no-js" data-19ax5a9jf="dingo"><!-- sp:feature:head-start -->\n<head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/>\n<!-- sp:end-feature:head-start -->\n\n<!-- sp:feature:cs-optimization -->\n<meta http-equiv=\'x-dns-prefetch-control\' content=\'on\'>\n<link rel="dns-prefetch" href="https://images-eu.ssl-images-amazon.com">\n<link rel="dns-prefetch" href="https://m.media-amazon.com">\n<link rel="dns-prefetch" href="https://completion.amazon.com">\n<!-- sp:end-feature:cs-optimization -->\n\n<!-- sp:feature:aui-assets -->\n<link rel="stylesheet" href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL.cs

In [81]:
page = response.text
soup = BeautifulSoup(page, 'lxml')

In [82]:
print(soup.prettify())

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo" lang="en-ae">
 <!-- sp:feature:head-start -->
 <head>
  <script>
   var aPageStart = (new Date()).getTime();
  </script>
  <meta charset="utf-8"/>
  <!-- sp:end-feature:head-start -->
  <!-- sp:feature:cs-optimization -->
  <meta content="on" http-equiv="x-dns-prefetch-control"/>
  <link href="https://images-eu.ssl-images-amazon.com" rel="dns-prefetch"/>
  <link href="https://m.media-amazon.com" rel="dns-prefetch"/>
  <link href="https://completion.amazon.com" rel="dns-prefetch"/>
  <!-- sp:end-feature:cs-optimization -->
  <!-- sp:feature:aui-assets -->
  <link href="https://images-eu.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41JZEtDv4tL.css,31Y8m1dzTdL.css,013z33uKh2L.css,017DsKjNQJL.css,0131vqwP5UL.css,41EWOOlBJ9L.css,11TIuySqr6L.css,01ElnPiDxWL.css,11bGSgD5pDL.css,01Dm5eKVxwL.css,01IdKcBuAdL.css,01y-XAlI+2L.css,21N4kUH7pxL.css,01oDR3IULNL.css,41CYNGpGlrL.css,01XPHJk60-L.css,114y0SIP+yL.css,21aPhFy+riL

In [83]:
soup.find_all('li', {'class':'zg-item-immersion'})[1].find_all('a')[1].text

'\n3.8 out of 5 stars\n'

In [84]:
def clean_num(s):
    """cleans text scraped from website
    
    Parameters:
    s (String): raw text

    Returns:
    String: cleaned digit text

    """ 

    if s is None:
        return s
    return "".join(re.findall('\d*\.?\d+',s))

def get_data(block, tag, class_text):
    """fetch data from tag and its associated class
    
    Parameters:
    block (int): Book item 
    tag (String): tag for element we want to fetch
    class_text (String): class for element we want to fetch

    Returns:
    String: data text fetched

    """ 
    try:
        return block.find(tag, class_ = class_text).text
    except AttributeError:
        return ""
    return

In [85]:
for i in (soup.find("li", "zg-item-immersion")):
    print(str.strip(get_data(i, "a", "a-link-normal")))
    print(get_data(i, "span", "a-icon-alt"))
    print(clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    print(get_data(i, "a","a-size-small a-link-normal"))
    print(clean_num(get_data(i, "a","a-size-small a-link-normal")))
    print(get_data(i, "span","p13n-sc-price"))
    print(clean_num(get_data(i, "span", "p13n-sc-price")))

SAMSUNG Galaxy Tab S7 11-inch Android Tablet 128GB Wi-Fi Bluetooth S Pen Fast Charging USB-C Port, Mystic Silver
4.7 out of 5 stars
4.7
1,307
1307
SAR 2,162.42
2162.42


In [86]:
products_list = []
for i in (soup.find_all("li", class_ = "zg-item-immersion")):
    pro_name = (str.strip(get_data(i, "a", "a-link-normal")))
    pro_rate= (get_data(i, "span", "a-icon-alt"))
    pro_rate_clean = (clean_num(get_data(i, "span", "a-icon-alt").split(" ")[0]))
    review_num = (get_data(i, "a","a-size-small a-link-normal"))
    review_num_clean = (clean_num(get_data(i, "a","a-size-small a-link-normal")))
    pro_price = (get_data(i, "span","p13n-sc-price"))
    pro_price_clean = (clean_num(get_data(i, "span", "p13n-sc-price")))
    
    headers = ['pro_name', 'pro_rate', 'pro_rate_clean','review_num',
              'review_num_clean', 'pro_price','pro_price_clean']
    products_dict = dict(zip(headers, [ pro_name,
                                    pro_rate,
                                    pro_rate_clean,
                                    review_num,
                                    review_num_clean, 
                                    pro_price,
                                    pro_price_clean]))
    products_list.append(products_dict)

In [87]:
products_df = pd.DataFrame(products_list).replace("",np.nan)  #convert list of dict to df
products_df

pro_name            pro_rate  \
0   SAMSUNG Galaxy Tab S7 11-inch Android Tablet 1...  4.7 out of 5 stars   
1   Lenovo Tab M10 (TB-X505X), 10.1 Inch Tablet, 1...  3.8 out of 5 stars   
2   Lenovo Tab M7 (TB-7305X) 7 inch Tablet, Wi-Fi ...  3.2 out of 5 stars   
3   SAMSUNG Galaxy Tab S7 11-inch Android Tablet 1...  4.7 out of 5 stars   
4   Datazone Kids tablet, Childern tablet 7.0 inch...  1.0 out of 5 stars   
5   Xiaomi Pad 5 11" Tablet, 256GB, 6GB RAM, Wi-Fi...  5.0 out of 5 stars   
6   2020 Apple iPad Air (10.9-inch, Wi-Fi, 256GB) ...  4.4 out of 5 stars   
7   HUAWEI MatePad T8 Tablet, 8 inch, 32GB 2GB RAM...                 NaN   
8   Microsoft Surface Pro 7 Tablet - 12.3 Inch, 10...  4.5 out of 5 stars   
9   Samsung Galaxy Tab S7 FE Tablet - 64GB, 4GB RA...  2.0 out of 5 stars   
10  Samsung Electronics Galaxy Tab S7 FE 2021 Andr...  4.5 out of 5 stars   
11  2021 Apple 10.2-inch iPad (Wi-Fi + Cellular, 2...  4.2 out of 5 stars   
12  SAMSUNG Galaxy Tab S7 11-inch Android Tablet 1...  4.7 out of 5 stars   
13  2021 Apple iPad Pro (11-inch, Wi-Fi, 256GB) - ...  4.6 out of 5 stars   
14  2021 Apple iPad Pro (12.9-inch, Wi-Fi, 256GB) ...  4.8 out of 5 stars   
15  2021 Apple iPad Pro (11-inch, Wi-Fi + Cellular...  4.6 out of 5 stars   
16  SAMSUNG Galaxy Tab S6, 10.5", 6G RAM, 128GB, L...  4.7 out of 5 stars   
17  Lume Cube Broadcast Lighting Kit | Self Broadc...  4.4 out of 5 stars   
18  Slim Folio Pro for iPad Pro 11-inch (1st and 2...  4.0 out of 5 stars   
19  Lenovo Yoga Smart Tablet, 10.1" FHD (1920x1200...                 NaN   
20  Samsung Galaxy Tab Active3 Enterprise Edition ...  4.1 out of 5 stars   
21  8" Windows Tablet with HDMI Port,1280x800 Touc...                 NaN   
22  2021 Apple iPad Pro (12.9-inch, Wi-Fi + Cellul...  4.8 out of 5 stars   
23  NEW Microsoft Surface Duo 256GB (Unlocked) - G...  4.1 out of 5 stars   
24  Lenovo Tab M10 FHD Plus 2nd GEN (TB-X606X), 10...  3.8 out of 5 stars   
25  SAMSUNG Galaxy Tab A7 Lite Tablet - 32GB, 3GB ...  3.2 out of 5 stars   
26  Alcatel 8052 TKEE Smart Tablet For Kids - 7 In...  2.6 out of 5 stars   
27  Lenovo Tab P11 (TB-J606L) 11 inch Tablet, Wi-F...  5.0 out of 5 stars   
28  brave 8" WiFi, 32GB ROM, 2GB RAM, Blue with Wi...                 NaN   
29  HUAWEI MatePad T 10 Kids Edition, 9.7’’ Tablet...                 NaN   
30  Lenovo M7 (TB-7305X) 7 Inch Tablet, Wi-Fi + Ce...  3.7 out of 5 stars   
31  2020 Apple iPad Air (10.9-inch, Wi-Fi + Cellul...  4.4 out of 5 stars   
32  Samsung Galaxy Tab S6 Lite 10.4", 64GB WiFi An...  4.3 out of 5 stars   
33  Samsung Galaxy Tab S7 FE 2021 Android Tablet 1...  4.5 out of 5 stars   
34  Lenovo Tab M10 HD 2nd Gen, 10.1"FHD Tablet, Me...  5.0 out of 5 stars   
35  Smart Tablets Datazone 7.0 inch Dual Camera Du...  2.0 out of 5 stars   
36  Lenosed G1, Education Kids Tablet,KARAOKE WITH...                 NaN   
37  Samsung Electronics Tab A7 Lite 8.7" Silver 32...  3.5 out of 5 stars   
38  Apple iPad Pro (12.9-inch, Wi-Fi + Cellular, 1...  5.0 out of 5 stars   
39  SAMSUNG Galaxy Tab S7+ Plus 12.4-inch Android ...  4.7 out of 5 stars   
40  2021 Apple iPad Pro (12.9-inch, Wi-Fi, 256GB) ...  4.8 out of 5 stars   
41    2021 Apple iPad mini (Wi-Fi, 256GB) - Starlight  4.1 out of 5 stars   
42  2021 Apple iPad mini (Wi-Fi + Cellular, 64GB) ...  4.1 out of 5 stars   
43  2020 Apple iPad Air (10.9-inch, Wi-Fi + Cellul...  4.4 out of 5 stars   
44  2021 Apple iPad Pro (12.9-inch, Wi-Fi, 512GB) ...  4.8 out of 5 stars   
45  AVITA Magus II 10.1" HD Tablet with Detachable...  4.0 out of 5 stars   
46     2021 Apple iPad mini (Wi-Fi, 64GB) - Starlight  4.1 out of 5 stars   
47  Samsung Galaxy Tab S6 Lite, 64GB, 4GB RAM, Wi-...  4.3 out of 5 stars   
48  Samsung Electronics Galaxy Tab S7 FE 2021 Andr...  4.5 out of 5 stars   
49  C idea Cm3000+ 10 inch Tablet,Face Unlock,Dual...  5.0 out of 5 stars   

   pro_rate_clean review_num review_num_clean     pro_price pro_price_clean  
0             4.7      1,307           